In [ ]:
YOUR_API_KEY = "insert_API_key"
base_drive_folder_path = 'drive/MyDrive/flood/korea/'

# General Imports

In [ ]:
!pip install -q lightning
!pip install -q torchinfo
!pip install -q comet-ml

In [ ]:



import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import torch.utils
torch.manual_seed(42)

import pandas as pd
from google.colab import drive
from pathlib import Path
from warnings import simplefilter

from tqdm import tqdm


import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
from sklearn.model_selection import train_test_split





drive.mount('/content/drive/')


Mounted at /content/drive/


In [ ]:
from lightning.pytorch.loggers import CometLogger



In [ ]:
simplefilter("ignore")

# Set Matplotlib defaults
plt.style.use("seaborn-whitegrid")
plt.rc("figure", autolayout=True, figsize=(11, 4))
plt.rc(
    "axes",
    labelweight="bold",
    labelsize="large",
    titleweight="bold",
    titlesize=16,
    titlepad=10,
)
plot_params = dict(
    color="0.75",
    style=".-",
    markeredgecolor="0.25",
    markerfacecolor="0.25",
)

plot_params2 = dict(
    color="red",
    style=".-",
    markeredgecolor="0.25",
    markerfacecolor="0.25",
)

%config InlineBackend.figure_format = 'retina'


def plot_multistep(y, every=1, ax=None, palette_kwargs=None):
    palette_kwargs_ = dict(palette='husl', n_colors=16, desat=None)
    if palette_kwargs is not None:
        palette_kwargs_.update(palette_kwargs)
    palette = sns.color_palette(**palette_kwargs_)
    if ax is None:
        fig, ax = plt.subplots()
    ax.set_prop_cycle(plt.cycler('color', palette))
    for date, preds in y[::every].iterrows():
        preds.index = pd.period_range(start=date, periods=len(preds), freq='H')
        preds.plot(ax=ax)
    return ax

# Dataset Pipelines

### Water Levels

In [ ]:
def prepare_df(dataf):
  dataf = (dataf
          .rename(columns={"관측 일시":"date", "01시":"H01", "02시":"H02", "03시":"H03", "04시":"H04", "05시":"H05", "06시":"H06", "07시":"H07", "08시":"H08", "09시":"H09", "10시":"H10","11시":"H11", "12시":"H12", "13시":"H13", "14시":"H14", "15시":"H15", "16시":"H16", "17시":"H17", "18시":"H18", "19시":"H19", "20시":"H20", "21시":"H21", "22시":"H22", "23시":"H23", "24시":"H24"})
          .drop([dataf.shape[0]-1,dataf.shape[0]-2]))
  dataf = pd.wide_to_long(dataf, ["H"], i="date", j="hour").reset_index().rename(columns={"H":"water_level"}).sort_values(by=['date', 'hour'])
  dataf.insert(2, 'datetime', pd.to_datetime(dataf['date'].astype(str) + ' ' +(dataf['hour']-1).astype(str) + ':00:00'))
  return (dataf
          .drop(columns=['hour', 'date'])
          )

def drop_bad_wl(dataf):
  dataf['water_level']=dataf['water_level'].astype(float)
  return (dataf
          .replace(0.0, np.nan)
          #.loc[(dataf['water_level']>0.0)]
          )


def add_station(dataf, name):
  dataf = dataf.rename(columns={'water_level':'water_level_'+name})
  return dataf

### Precipitations

In [ ]:
def prepare_df_preci(dataf):
  dataf = (dataf
          .rename(columns={"관측 일시":"date", "01시":"H01", "02시":"H02", "03시":"H03", "04시":"H04", "05시":"H05", "06시":"H06", "07시":"H07", "08시":"H08", "09시":"H09", "10시":"H10","11시":"H11", "12시":"H12", "13시":"H13", "14시":"H14", "15시":"H15", "16시":"H16", "17시":"H17", "18시":"H18", "19시":"H19", "20시":"H20", "21시":"H21", "22시":"H22", "23시":"H23", "24시":"H24"})
          .drop([dataf.shape[0]-1,dataf.shape[0]-2])
          )
  dataf = pd.wide_to_long(dataf, ["H"], i="date", j="hour").reset_index().rename(columns={"H":"precipitation"}).sort_values(by=['date', 'hour'])
  dataf.insert(2, 'datetime', pd.to_datetime(dataf['date'].astype(str) + ' ' +(dataf['hour']-1).astype(str) + ':00:00'))
  return (dataf
          .drop(columns=['hour', 'date'])
          )

def drop_bad_preci(dataf):
  dataf['precipitation']=dataf['precipitation'].astype(float)
  return (dataf
          .loc[(dataf['precipitation']>=0.0)])


def add_station_preci(dataf, name):
  dataf = dataf.rename(columns={'precipitation':'precipitation_'+name})
  return dataf


### Weather

In [ ]:
def prepare_df_temp(dataf):
  dataf = dataf.drop(columns=['Unnamed: 0'])
  dataf.insert(1, 'datetime', pd.to_datetime(df_temp['date'].astype(str)))
  dataf = dataf.drop(columns=['date'])
  return dataf

# General file preparation

### File paths

In [ ]:
xls_path_base = base_drive_folder_path + 'wl/'
wl_station = ['1007639','1007641','1007635','1007633','1007634','1007625']
xls_path_base_preci = base_drive_folder_path + 'preci/'
preci_station = ['10074030_preci', '10074070_preci', '10054010_preci']

xls_path_base_temp = base_drive_folder_path + 'temp/raw_temp_clean.xlsx'

## Data Imports

### Water levels

In [ ]:
first_ts = []
list_of_df = []
for station_id, station_name in enumerate(wl_station):
  xls_path = xls_path_base + station_name + '.xls'
  df = (pd.read_excel(xls_path)
  .pipe(prepare_df)
  .pipe(drop_bad_wl)
  .pipe(add_station, station_name)
  )
  df.reset_index(inplace=True, drop=True)
  df = df.set_index(df['datetime'])
  first_ts_val = df.values[0,0]
  list_of_df.append(df)
  first_ts.append(first_ts_val)

for df_id in range(len(list_of_df)):
  list_of_df[df_id] = list_of_df[df_id].loc[(list_of_df[df_id]['datetime']>max(first_ts))]
  if df_id:
    complete_df = pd.concat([complete_df, list_of_df[df_id]], axis=1)
  else:
    complete_df = list_of_df[df_id].copy()
complete_df_bu = complete_df.copy()
complete_df = complete_df.replace(r'^s*$', np.nan, regex = True)  # Replace blanks by NaN
complete_df=complete_df.drop(columns=['datetime'])
complete_df_inter = complete_df.copy().astype('float')
for col_name in complete_df_inter.columns:
  complete_df_inter[col_name] = complete_df_inter[col_name].interpolate()
complete_df_inter.dropna(inplace=True)
complete_df.dropna(inplace = True)


### Weather

In [ ]:
df_temp = pd.read_excel(xls_path_base_temp)
complete_df_temp = df_temp.pipe(prepare_df_temp)
complete_df_temp = complete_df_temp.loc[(complete_df_temp['datetime']>=complete_df_inter.index.min())]
complete_df_temp = complete_df_temp.loc[(complete_df_temp['datetime']<=complete_df_inter.index.max())]

complete_df_temp.reset_index(inplace=True, drop=True)
complete_df_temp = complete_df_temp.set_index(complete_df_temp['datetime'])
complete_df_temp = complete_df_temp.drop(columns=['datetime'])

#fill the gaps
complete_df_temp = complete_df_temp.resample('H').sum()
for col_name in complete_df_temp.columns:
  complete_df_temp[col_name] = complete_df_temp[col_name].interpolate()
complete_df_temp.dropna(inplace=True)

### Precipitations

In [ ]:
first_ts_preci = []
list_of_df_preci = []
for station_id, station_name in enumerate(preci_station):
  xls_path_preci = xls_path_base_preci + station_name + '.xlsx'
  df_preci = (pd.read_excel(xls_path_preci)
    .pipe(prepare_df_preci)
    .pipe(drop_bad_preci)
    .pipe(add_station_preci, station_name)
  )
  df_preci.reset_index(inplace=True, drop=True)
  df_preci = df_preci.set_index(df_preci['datetime'])
  first_ts_val_preci = df_preci.values[0,0]
  list_of_df_preci.append(df_preci.copy())
  first_ts_preci.append(first_ts_val_preci)

for df_id in range(len(list_of_df_preci)):
  list_of_df_preci[df_id] = list_of_df_preci[df_id].loc[(list_of_df_preci[df_id]['datetime']>=(complete_df_inter.index.min()))]

  if df_id:
    complete_df_preci = pd.concat([complete_df_preci, list_of_df_preci[df_id]], axis=1)
  else:
    complete_df_preci = list_of_df_preci[df_id].copy()
complete_df_preci_bu = complete_df_preci.copy()
complete_df_preci = complete_df_preci.replace(r'^s*$', np.nan, regex = True)  # Replace blanks by NaN
complete_df_preci= complete_df_preci.drop(columns=['datetime'])

for col_name in complete_df_preci.columns:
  complete_df_preci[col_name] = complete_df_preci[col_name].interpolate()

complete_df_preci.dropna(inplace=True)
#complete_df.dropna(inplace = True)

### Checks

#### Sizes Checks

In [ ]:
print(complete_df_preci.index.difference(complete_df_inter.index))
print(complete_df_inter.index.difference(complete_df_preci.index))
print(complete_df_temp.index.difference(complete_df_inter.index))

print(complete_df_temp.shape)
print(complete_df_preci.shape)
print(complete_df_inter.shape)

DatetimeIndex([], dtype='datetime64[ns]', name='datetime', freq=None)
DatetimeIndex([], dtype='datetime64[ns]', name='datetime', freq='H')
DatetimeIndex([], dtype='datetime64[ns]', name='datetime', freq='H')
(83819, 3)
(83819, 3)
(83819, 6)


#### Gaps checks

Water Level

In [ ]:
mask_inter = complete_df_inter.index.to_series().diff() > pd.Timedelta('01:00:00')
mask_inter[mask_inter].index

DatetimeIndex([], dtype='datetime64[ns]', name='datetime', freq='H')

Precipitations

In [ ]:
mask_int_preci = complete_df_preci.index.to_series().diff() > pd.Timedelta('01:00:00')
mask_int_preci[mask_int_preci].index

DatetimeIndex([], dtype='datetime64[ns]', name='datetime', freq=None)

Weather


In [ ]:
mask_int_temp = complete_df_temp.index.to_series().diff() > pd.Timedelta('01:00:00')
mask_int_temp[mask_int_temp].index

DatetimeIndex([], dtype='datetime64[ns]', name='datetime', freq='H')

# Forecasting

## General Functions Definition

In [ ]:
def compute_losses(y_train, y_fit, y_test, y_pred):
  train_mae = mean_absolute_error(y_train, y_fit)
  test_mae = mean_absolute_error(y_test, y_pred)

  train_rmse = mean_squared_error(y_train, y_fit, squared=False)
  test_rmse = mean_squared_error(y_test, y_pred, squared=False)

  def nse(targets, predictions):
      return (1-(np.sum((targets-predictions)**2)/np.sum((targets-np.mean(targets, axis=0))**2))).mean(axis=0)

  train_nse = nse(y_train, y_fit)
  test_nse = nse(y_test, y_pred)

  print((f"Training:\n MAE: {train_mae:.2f} MSE: {train_rmse:.2f} NSE: {train_nse:.2f}"))
  print((f"Testing:\n MAE: {test_mae:.2f} MSE: {test_rmse:.2f} NSE: {test_nse:.2f}\n"))


In [ ]:
# convert series to supervised learning
def series_to_supervised(data_in, n_in=1, n_out=1, dropnan=True):
  data = data_in.copy()
  n_vars = data.shape[1]
  cols, names = list(), list()
  # input sequence (t-n, ... t-1)
  for i in range(n_in, 0, -1):
    cols.append(data.shift(i))
    names += [('%s(t-%d)' % (data.columns[j], i)) for j in range(n_vars)]
  # forecast sequence (t, t+1, ... t+n)
  for i in range(0, n_out):
    cols.append(data.shift(-i))
    if i == 0:
      names += [('%s(t)' % (data.columns[j])) for j in range(n_vars)]
    else:
      names += [('%s(t+%d)' % (data.columns[j], i)) for j in range(n_vars)]
  # put it all together
  agg = pd.concat(cols, axis=1)
  agg.columns = names
  # drop rows with NaN values
  if dropnan:
    agg.dropna(inplace=True)
  return agg


In [ ]:
class MinMaxScale:

  def __init__(self, dataf, ul=1, ll=0):
    self.min = dataf.min()
    self.max = dataf.max()
    self.UL = ul
    self.LL = ll

  def NormMM(self, dataf):
    return self.LL+(self.UL-self.LL)*(dataf - self.min)/(self.max-self.min)

  def DeNormMM(self, dataf, station_filter):
    return (dataf - self.LL) * (self.max-self.min).filter(regex=station_filter).values[0]/(self.UL-self.LL) + self.min.filter(regex=station_filter).values[0]


## General functions

In [ ]:
def prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, pred_station, predict_station_list):

  # split into input and outputs
  train_X = reframed_train.iloc[:, :(past_ts+1)*nbr_features]
  train_y = reframed_train.iloc[:, (past_ts+1)*nbr_features:]

  test_X = reframed_test.iloc[:, :(past_ts+1)*nbr_features]
  test_y = reframed_test.iloc[:, (past_ts+1)*nbr_features:]

  if predict_station_list is not None:
    past_train_x, past_test_x, past_train_y, past_test_y = None, None, None, None
    for id_filter in predict_station_list:

      tmp_train_x = (train_X.filter(regex=id_filter)).values
      tmp_train_y = (train_y.filter(regex=id_filter)).values

      tmp_test_x = (test_X.filter(regex=id_filter)).values
      tmp_test_y = (test_y.filter(regex=id_filter)).values

      if past_train_x is None:
        past_train_x = tmp_train_x.copy()
        past_train_y = tmp_train_y.copy()
        past_test_x = tmp_test_x.copy()
        past_test_y = tmp_test_y.copy()

      else:
        past_train_x = np.concatenate((past_train_x,tmp_train_x), axis=1)
        past_train_y = np.concatenate((past_train_y,tmp_train_y), axis=1)
        past_test_x = np.concatenate((past_test_x,tmp_test_x), axis=1)
        past_test_y = np.concatenate((past_test_y,tmp_test_y), axis=1)

    nbr_features = len(predict_station_list)+1

  else:
    past_train_x = train_X.drop(train_X.filter(regex=pred_station).columns,axis=1).values
    past_train_y = train_y.drop(train_y.filter(regex=pred_station).columns,axis=1).values

    past_test_x = test_X.drop(test_X.filter(regex=pred_station).columns,axis=1).values
    past_test_y = test_y.drop(test_y.filter(regex=pred_station).columns,axis=1).values

  train_X = train_X.filter(regex=pred_station).values
  train_y = train_y.filter(regex=pred_station).values
  test_X_pd = test_X.filter(regex=pred_station)
  test_X = test_X_pd.values
  test_y = test_y.filter(regex=pred_station).values

  # reshape input to be 3D [samples, timesteps, features]
  train_X = train_X.reshape((train_X.shape[0], past_ts+1, 1))
  past_train_x = past_train_x.reshape((past_train_x.shape[0], past_ts+1, nbr_features-1), order='F')

  test_X = test_X.reshape((test_X.shape[0], past_ts+1, 1))
  past_test_x = past_test_x.reshape((past_test_x.shape[0], past_ts+1, nbr_features-1), order='F')


  return train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd

In [ ]:
def prepare_past_stages_ED(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, pred_station, predict_station_list):

  # split into input and outputs
  train_X_hindcast = reframed_train.iloc[:, :(past_ts+1)*nbr_features]
  train_X_forecast = reframed_train.iloc[:, (past_ts)*nbr_features:]
  train_y = reframed_train.iloc[:, (past_ts+1)*nbr_features:]

  test_X = reframed_test.iloc[:, :(past_ts+1)*nbr_features]
  test_y = reframed_test.iloc[:, (past_ts+1)*nbr_features:]

  if predict_station_list is not None:
    past_train_x_hindcast, past_train_x_forecast, past_test_x, past_train_y, past_test_y = None, None, None, None, None
    for id_filter in predict_station_list:

      tmp_train_x_hindcast = (train_X_hindcast.filter(regex=id_filter)).values
      tmp_train_x_forecast = (train_X_forecast.filter(regex=id_filter)).values
      tmp_train_y = (train_y.filter(regex=id_filter)).values

      tmp_test_x = (test_X.filter(regex=id_filter)).values
      tmp_test_y = (test_y.filter(regex=id_filter)).values

      if past_train_x_hindcast is None:
        past_train_x_forecast = tmp_train_x_forecast.copy()
        past_train_x_hindcast = tmp_train_x_hindcast.copy()
        past_train_y = tmp_train_y.copy()
        past_test_x = tmp_test_x.copy()
        past_test_y = tmp_test_y.copy()

      else:
        past_train_x_hindcast = np.concatenate((past_train_x_hindcast,tmp_train_x_hindcast), axis=1)
        past_train_x_forecast = np.concatenate((past_train_x_forecast,tmp_train_x_forecast), axis=1)

        past_train_y = np.concatenate((past_train_y,tmp_train_y), axis=1)
        past_test_x = np.concatenate((past_test_x,tmp_test_x), axis=1)
        past_test_y = np.concatenate((past_test_y,tmp_test_y), axis=1)
    nbr_features = len(predict_station_list)+1

  else:
    past_train_x_hindcast = train_X_hindcast.drop(train_X_hindcast.filter(regex=pred_station).columns,axis=1).values
    past_train_x_forecast = train_X_forecast.drop(train_X_forecast.filter(regex=pred_station).columns,axis=1).values

    past_train_y = train_y.drop(train_y.filter(regex=pred_station).columns,axis=1).values

    past_test_x = test_X.drop(test_X.filter(regex=pred_station).columns,axis=1).values
    past_test_y = test_y.drop(test_y.filter(regex=pred_station).columns,axis=1).values

  train_X_hindcast = train_X_hindcast.filter(regex=pred_station).values
  train_X_forecast = train_X_forecast.filter(regex=pred_station).values

  train_y = train_y.filter(regex=pred_station).values
  test_X_pd = test_X.filter(regex=pred_station)
  test_X = test_X_pd.values
  test_y = test_y.filter(regex=pred_station).values

  # reshape input to be 3D [samples, timesteps, features]
  train_X_hindcast = train_X_hindcast.reshape((train_X_hindcast.shape[0], past_ts+1, 1))
  print(past_train_x_hindcast[0])
  past_train_x_hindcast = past_train_x_hindcast.reshape((past_train_x_hindcast.shape[0], past_ts+1, nbr_features-1))
  print(past_train_x_hindcast[0, :, 0])

  train_X_forecast = train_X_forecast.reshape((train_X_forecast.shape[0], predict_ts, 1))
  past_train_x_forecast = past_train_x_forecast.reshape((past_train_x_forecast.shape[0], predict_ts, nbr_features-1))

  test_X = test_X.reshape((test_X.shape[0], past_ts+1, 1))
  past_test_x = past_test_x.reshape((past_test_x.shape[0], past_ts+1, nbr_features-1))


  return train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd

In [ ]:
def prepare_past_stages_test(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, pred_station, predict_station_list):

  # split into input and outputs
  train_X_hindcast = reframed_train.iloc[:, :(past_ts+1)*nbr_features]
  train_X_forecast = reframed_train.iloc[:, (past_ts)*nbr_features:]
  train_y = reframed_train.iloc[:, (past_ts+1)*nbr_features:]

  test_X = reframed_test.iloc[:, :(past_ts+1)*nbr_features]
  test_y = reframed_test.iloc[:, (past_ts+1)*nbr_features:]

  if predict_station_list is not None:
    past_train_x_hindcast, past_train_x_forecast, past_test_x, past_train_y, past_test_y = None, None, None, None, None
    for id_filter in predict_station_list:

      tmp_train_x_hindcast = (train_X_hindcast.filter(regex=id_filter))
      tmp_train_x_forecast = (train_X_forecast.filter(regex=id_filter))
      tmp_train_y = (train_y.filter(regex=id_filter))

      tmp_test_x = (test_X.filter(regex=id_filter))
      tmp_test_y = (test_y.filter(regex=id_filter))

      if past_train_x_hindcast is None:
        past_train_x_forecast = tmp_train_x_forecast.copy()
        past_train_x_hindcast = tmp_train_x_hindcast.copy()
        past_train_y = tmp_train_y.copy()
        past_test_x = tmp_test_x.copy()
        past_test_y = tmp_test_y.copy()

      else:

        past_train_x_hindcast = pd.concat([past_train_x_hindcast,tmp_train_x_hindcast], axis=1, sort=False)
        past_train_x_forecast = pd.concat([past_train_x_forecast,tmp_train_x_forecast], axis=1, sort=False)

        past_train_y = pd.concat([past_train_y,tmp_train_y], axis=1, sort=False)
        past_test_x = pd.concat([past_test_x,tmp_test_x], axis=1, sort=False)
        past_test_y = pd.concat([past_test_y,tmp_test_y], axis=1, sort=False)

    nbr_features = len(predict_station_list)+1

  else:
    past_train_x_hindcast = train_X_hindcast.drop(train_X_hindcast.filter(regex=pred_station).columns,axis=1)
    past_train_x_forecast = train_X_forecast.drop(train_X_forecast.filter(regex=pred_station).columns,axis=1)

    past_train_y = train_y.drop(train_y.filter(regex=pred_station).columns,axis=1)

    past_test_x = test_X.drop(test_X.filter(regex=pred_station).columns,axis=1)
    past_test_y = test_y.drop(test_y.filter(regex=pred_station).columns,axis=1)

  train_X_hindcast = train_X_hindcast.filter(regex=pred_station)
  train_X_forecast = train_X_forecast.filter(regex=pred_station)

  train_y = train_y.filter(regex=pred_station)
  test_X_pd = test_X.filter(regex=pred_station)
  test_X = test_X_pd
  test_y = test_y.filter(regex=pred_station)

  # reshape input to be 3D [samples, timesteps, features]
  #train_X_hindcast = train_X_hindcast.reshape((train_X_hindcast.shape[0], past_ts+1, 1))
  #past_train_x_hindcast = past_train_x_hindcast.reshape((past_train_x_hindcast.shape[0], past_ts+1, nbr_features-1))

  #train_X_forecast = train_X_forecast.reshape((train_X_forecast.shape[0], predict_ts, 1))
  #past_train_x_forecast = past_train_x_forecast.reshape((past_train_x_forecast.shape[0], predict_ts, nbr_features-1))

  #test_X = test_X.reshape((test_X.shape[0], past_ts+1, 1))
  #past_test_x = past_test_x.reshape((past_test_x.shape[0], past_ts+1, nbr_features-1))


  return train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd

In [ ]:
def prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, pred_station, predict_station_list):

  # split into input and outputs
  train_X_hindcast = reframed_train.iloc[:, :(past_ts+1)*nbr_features]
  train_X_forecast = reframed_train.iloc[:, (past_ts)*nbr_features:]
  train_y = reframed_train.iloc[:, (past_ts+1)*nbr_features:]

  test_X = reframed_test.iloc[:, :(past_ts+1)*nbr_features]
  test_y = reframed_test.iloc[:, (past_ts+1)*nbr_features:]

  if predict_station_list is not None:
    past_train_x_hindcast, past_train_x_forecast, past_test_x, past_train_y, past_test_y = None, None, None, None, None
    for id_filter in predict_station_list:

      tmp_train_x_hindcast = (train_X_hindcast.filter(regex=id_filter)).values
      tmp_train_x_forecast = (train_X_forecast.filter(regex=id_filter)).values
      tmp_train_y = (train_y.filter(regex=id_filter)).values

      tmp_test_x = (test_X.filter(regex=id_filter)).values
      tmp_test_y = (test_y.filter(regex=id_filter)).values

      if past_train_x_hindcast is None:
        past_train_x_forecast = tmp_train_x_forecast.copy()
        past_train_x_hindcast = tmp_train_x_hindcast.copy()
        past_train_y = tmp_train_y.copy()
        past_test_x = tmp_test_x.copy()
        past_test_y = tmp_test_y.copy()

      else:
        past_train_x_hindcast = np.concatenate((past_train_x_hindcast,tmp_train_x_hindcast), axis=1)
        past_train_x_forecast = np.concatenate((past_train_x_forecast,tmp_train_x_forecast), axis=1)

        past_train_y = np.concatenate((past_train_y,tmp_train_y), axis=1)
        past_test_x = np.concatenate((past_test_x,tmp_test_x), axis=1)
        past_test_y = np.concatenate((past_test_y,tmp_test_y), axis=1)
    nbr_features = len(predict_station_list)+1

  else:
    past_train_x_hindcast = train_X_hindcast.drop(train_X_hindcast.filter(regex=pred_station).columns,axis=1).values
    past_train_x_forecast = train_X_forecast.drop(train_X_forecast.filter(regex=pred_station).columns,axis=1).values

    past_train_y = train_y.drop(train_y.filter(regex=pred_station).columns,axis=1).values

    past_test_x = test_X.drop(test_X.filter(regex=pred_station).columns,axis=1).values
    past_test_y = test_y.drop(test_y.filter(regex=pred_station).columns,axis=1).values

  train_X_hindcast = train_X_hindcast.filter(regex=pred_station).values
  train_X_forecast = train_X_forecast.filter(regex=pred_station).values

  train_y = train_y.filter(regex=pred_station).values
  test_X_pd = test_X.filter(regex=pred_station)
  test_X = test_X_pd.values
  test_y = test_y.filter(regex=pred_station).values

  # reshape input to be 3D [samples, timesteps, features]
  train_X_hindcast = train_X_hindcast.reshape((train_X_hindcast.shape[0], past_ts+1, 1))
  past_train_x_hindcast = past_train_x_hindcast.reshape((past_train_x_hindcast.shape[0], past_ts+1, nbr_features-1), order='F')

  train_X_forecast = train_X_forecast.reshape((train_X_forecast.shape[0], predict_ts, 1))
  past_train_x_forecast = past_train_x_forecast.reshape((past_train_x_forecast.shape[0], predict_ts, nbr_features-1), order='F')

  test_X = test_X.reshape((test_X.shape[0], past_ts+1, 1))
  past_test_x = past_test_x.reshape((past_test_x.shape[0], past_ts+1, nbr_features-1), order='F')


  return train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd

In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=7
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = False
fuse_input = True


extra_in = [complete_df_preci, complete_df_temp]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station
      other_station_id += list(complete_df_temp.columns)

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    basic = False
    if basic:
      train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

      if fuse_input:
        train_X = np.concatenate((train_X,past_train_x), axis=2)
        test_X = np.concatenate((test_X,past_test_x), axis=2)

      y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
      y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    else:
      train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test,  predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)
      if fuse_input:
        train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
        train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
        test_X = np.concatenate((test_X,past_test_x), axis=2)
      train_y_hindcast = train_X_forecast[:,0,:].copy()

      y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
      y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

      if train or load_model:
        train_X_hindcast  = torch.tensor(train_X_hindcast).float()
        train_X_forecast  = torch.tensor(train_X_forecast).float()

        train_y = torch.tensor(train_y).float()
        train_y_hindcast = torch.tensor(train_y_hindcast).float()

        test_X =  torch.tensor(test_X).float()
        test_y = torch.tensor(test_y).float()

  break

## Models definition

In [ ]:
import lightning.pytorch as L
from torchinfo import summary
from lightning.pytorch.callbacks import ModelCheckpoint

from pathlib import Path

In [ ]:

#creating a new directory called pythondirectory

class MultiLSTM(L.LightningModule):
    def __init__(self, input_size=1, hidden_size=256, num_layers=2, forecast_length = 1, rnn_type=['LSTM']):
        super(MultiLSTM, self).__init__()

        self.rnn_layers = []
        for l_id, layer_type in enumerate(rnn_type):
          if 'LSTM' in layer_type:
            self.rnn_layers.append(nn.LSTM(input_size=input_size, hidden_size=hidden_size[l_id], num_layers=num_layers[l_id], batch_first=True))
          elif 'GRU' in layer_type:
            self.rnn_layers.append(nn.GRU(input_size=input_size, hidden_size=hidden_size[l_id], num_layers=num_layers[l_id], batch_first=True))

        self.linear = nn.Linear(hidden_size[-1], forecast_length)
        self.hidden_size= hidden_size[-1]

        self.train_loss = 0
        self.nbr_iter = 0
        self.val_loss = 0
        self.nbr_iter_val = 0

    def training_step(self, batch):
        x,y = batch

        for layer_id, layer in enumerate(self.rnn_layers):
          print(x.shape)
          if layer_id:
            x, (h,c) = layer(x)
          else:
            x, (h,c) = layer(x)

        x = x[:, -1, :]
        pred = self.linear(x)
        loss = nn.functional.mse_loss(pred, y)
        self.train_loss += loss
        self.nbr_iter += 1
        self.log("train_loss", loss)
        return loss

    # Only for inference
    def forward(self, batch):
        x,y = batch

        for layer_id, layer in enumerate(self.rnn_layers):
          x, (h,c) = layer(x)

        x = x[:, -1, :]
        x = self.linear(x)
        return x

    def validation_step(self, batch, batch_idx):
        x,y = batch
        for layer_id, layer in enumerate(self.rnn_layers):
          print(x.shape)
          x, (h,c) = layer(x)

        x = x[:, -1, :]
        pred = self.linear(x)
        loss = nn.functional.mse_loss(pred, y)
        self.log("val_loss", loss)
        self.val_loss += loss
        self.nbr_iter_val += 1



    def on_train_epoch_end(self):
      loss = self.train_loss / self.nbr_iter
      #print(f'Traning loss: {loss}')
      self.train_loss = 0
      self.nbr_iter = 0

    def on_train_epoch_start(self):
      if self.nbr_iter_val:
        loss = self.val_loss / self.nbr_iter_val
        #print(f'Validation loss: {loss}')
        self.val_loss = 0
        self.nbr_iter_val = 0

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=1e-3)

class LitFLSTM(L.LightningModule):
    def __init__(self, input_size=10, hidden_size=256, num_layers=2, forecast_length = 4, rnn_type=['LSTM']):
        super().__init__()
        for layer_type in rnn_type:
          if 'LSTM' in layer_type:
            self.rnn_layer = nn.LSTM(input_size=input_size, hidden_size=hidden_size, num_layers=num_layers, batch_first=True)
          elif 'GRU' in layer_type:
            self.rnn_layer = nn.GRU(input_size=input_size, hidden_size=hidden_size, num_layers=num_layers, batch_first=True)
        self.linear = nn.Linear(hidden_size, forecast_length)

        self.train_loss = 0
        self.nbr_iter = 0
        self.val_loss = 0
        self.nbr_iter_val = 0

    # Only for inference
    def forward(self, batch):
        x,_ = batch
        x, _ = self.rnn_layer(x)
        x = x[:, -1, :]
        x = self.linear(x)
        return x

    def validation_step(self, batch, batch_idx):
        x, y = batch
        x, _ = self.rnn_layer(x)
        x = x[:, -1, :]
        pred = self.linear(x)
        loss = nn.functional.mse_loss(pred, y)
        self.log("val_loss", loss)
        self.val_loss += loss
        self.nbr_iter_val += 1

    def training_step(self, batch, batch_idx):
        x, y = batch
        x, _ = self.rnn_layer(x)
        x = x[:, -1, :]
        pred = self.linear(x)
        loss = nn.functional.mse_loss(pred, y)
        self.train_loss += loss
        self.nbr_iter += 1
        self.log("train_loss", loss)
        return loss

    def on_train_epoch_end(self):
      loss = self.train_loss / self.nbr_iter
      #print(f'Traning loss: {loss}')
      self.log("mean_train_loss", loss)
      self.train_loss = 0
      self.nbr_iter = 0

    def on_train_epoch_start(self):
      if self.nbr_iter_val:
        loss = self.val_loss / self.nbr_iter_val
        #print(f'Validation loss: {loss}')
        self.log("mean_val_loss", loss)
        self.val_loss = 0
        self.nbr_iter_val = 0

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=1e-3)

def define_model_L(nbr_features, predict_ts, batch_size, hidden_size, rnn_type=['LSTM'], num_layers=2):
  print(f'Model type: {rnn_type}')
  if len(rnn_type) > 1:
    lstm_model = MultiLSTM(input_size=nbr_features, hidden_size=hidden_size, num_layers=num_layers, forecast_length = predict_ts, rnn_type=rnn_type)
  else:
    lstm_model = LitFLSTM(input_size=nbr_features, hidden_size=hidden_size, num_layers=num_layers, forecast_length = predict_ts, rnn_type=rnn_type)
  return lstm_model

def training_model_L(model, batch_size, train_X, train_y, test_X, test_y, nbr_epoch = 30, save_epoch = 10, save_path=None, resume_path=None):
  savename_path = base_drive_folder_path + 'weights/' + save_path + '/'
  Path(savename_path).mkdir(parents=True, exist_ok=True)

  checkpoint_callback = ModelCheckpoint(dirpath=savename_path,
                                        every_n_epochs=save_epoch)

  trainer = L.Trainer(max_epochs=nbr_epoch,
                      enable_model_summary=True,
                      callbacks=[checkpoint_callback],
                      val_check_interval=int(train_X.shape[0]/batch_size),
                      logger=comet_logger)

  loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=True, batch_size=batch_size)
  test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=batch_size)

  if resume_path is None:
    trainer.fit(model=model, train_dataloaders=loader, val_dataloaders=test_loader)
  else:
    trainer.fit(model=model, train_dataloaders=loader, val_dataloaders=test_loader, ckpt_path=resume_path)

  loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
  test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)
  y_fit = trainer.predict(dataloaders=loader)
  y_pred = trainer.predict(dataloaders=test_loader)

  return y_fit, y_pred, model

In [ ]:
import random
class LitHindForeHandOff(L.LightningModule):
    def __init__(self,
                 input_size=10,
                 hindcast_hidden_size = 256,
                 hindcast_num_layers = 2,
                 forecast_hidden_size=256,
                 forecast_num_layers = 2,
                 handoff_hidden_size=256,
                 forecast_length = 10,
                 fuse_loss = False,
                 dropout_prob=0.,
                 head_type='regression',
                 rnn_type='LSTM',
                 teacher_forcing_ratio = .5):
        super().__init__()

        self.forecast_length = forecast_length
        self.nbr_features = input_size
        self.hindcast_hidden_size = hindcast_hidden_size
        self.hindcast_num_layers = hindcast_num_layers

        if rnn_type == 'LSTM':
          self.hindcast_lstm = nn.LSTM(
              input_size=input_size,
              hidden_size=self.hindcast_hidden_size,
              num_layers=self.hindcast_num_layers,
              batch_first=True
              )
        elif rnn_type == 'GRU':
          self.hindcast_lstm = nn.GRU(
              input_size=input_size,
              hidden_size=self.hindcast_hidden_size,
              num_layers=self.hindcast_num_layers,
              batch_first=True
              )

        self.forecast_hidden_size = forecast_hidden_size
        self.forecast_num_layers = forecast_num_layers

        if rnn_type == 'LSTM':
          self.forecast_lstm = nn.LSTM(
              input_size=input_size,
              hidden_size=self.forecast_hidden_size,
              num_layers=self.forecast_num_layers,
              batch_first=True
              )
        elif rnn_type == 'GRU':
          self.forecast_lstm = nn.GRU(
              input_size=input_size,
              hidden_size=self.forecast_hidden_size,
              num_layers=self.forecast_num_layers,
              batch_first=True
              )


        if handoff_hidden_size is not None:
          self.handoff_net = nn.Sequential(
              *[nn.Linear(self.hindcast_hidden_size*2, handoff_hidden_size),
              nn.ReLU(),
              nn.Dropout(p=0.)]
              )

          self.handoff_linear = nn.Sequential(
              *[nn.Linear(handoff_hidden_size, self.forecast_hidden_size*2),
              nn.Dropout(p=0.)]
              )
        else:
          self.handoff_net = None

        self.dropout = nn.Dropout(p=dropout_prob)

        if head_type == 'regression':
          self.hindcast_head = nn.Sequential(nn.Linear(self.hindcast_hidden_size, input_size))#, nn.ReLU())
          self.forecast_head = nn.Sequential(nn.Linear(self.forecast_hidden_size, self.nbr_features))#, nn.ReLU())

        self.rnn_type = rnn_type

        self.fuse_loss = fuse_loss

        self.teacher_forcing_ratio = teacher_forcing_ratio

        self.train_loss_f = 0
        self.train_loss_h = 0
        self.nbr_iter = 0
        self.val_loss = 0

        self.val_loss_f = 0
        self.val_loss_h = 0
        self.nbr_iter_val = 0

    def _forward_path_GRU(self, batch, training):
        if len(batch) == 2:
          x_h, y_f = batch
          y_h = y_f[:,0]
        else:
          x_h, x_f, y_h, y_f = batch

        # run the hindcast lstm
        lstm_output_hindcast, h_n_hindcast = self.hindcast_lstm(x_h)

        # handoff initial state to forecast lstm
        if self.handoff_net is not None:
          x = self.handoff_net(torch.cat([h_n_hindcast, c_n_hindcast], -1))
          initial_state = self.handoff_linear(x)
          h_n_handoff, c_n_handoff = initial_state.chunk(2, -1)
          h_n_handoff = h_n_handoff.contiguous()
        else:
          h_n_handoff = h_n_hindcast.contiguous()

        # DECODER
        if training:
            input = torch.unsqueeze(x_f[:,0,:], dim=1)
        else:
            input = torch.unsqueeze(x_h[:,-1,:], dim=1)

        lstm_output_forecast = torch.zeros(x_h.shape[0], self.forecast_length, self.nbr_features).to('cuda')
        hidden = h_n_handoff
        lstm_output_forecast[:,0] = input[:,0,:]
        for t in range(1, self.forecast_length):

            #insert input token embedding, previous hidden and previous cell states
            #receive output tensor (predictions) and new hidden and cell states
            output, hidden = self.forecast_lstm(input, hidden)
            #place predictions in a tensor holding predictions for each token

            output = self.forecast_head(output)
            lstm_output_forecast[:,t] = output[:,0,:]

            if training:
              #decide if we are going to use teacher forcing or not
              teacher_force = random.random() < self.teacher_forcing_ratio

              #get the highest predicted token from our predictions

              #if teacher forcing, use actual next token as next input
              #if not, use predicted token
              input = torch.unsqueeze(x_f[:,t,:], dim=1) if teacher_force else output
            else:
              input = output
        # run forecast lstm

        # run heads for hindcast and forecast
        y_hindcast = lstm_output_forecast[:,0,0]#self.hindcast_head(self.dropout(lstm_output_hindcast))[:,-1,0]

        y_forecast = lstm_output_forecast[:,:,0]

        return y_hindcast, y_forecast

    def _forward_path_LSTM(self, batch, training):
        if len(batch) == 2:
          x_h, y_f = batch
          y_h = y_f[:,0]
        else:
          x_h, x_f, y_h, y_f = batch

        # run the hindcast lstm
        lstm_output_hindcast, (h_n_hindcast, c_n_hindcast) = self.hindcast_lstm(x_h)

        # handoff initial state to forecast lstm
        if self.handoff_net is not None:
          x = self.handoff_net(torch.cat([h_n_hindcast, c_n_hindcast], -1))
          initial_state = self.handoff_linear(x)
          h_n_handoff, c_n_handoff = initial_state.chunk(2, -1)
          h_n_handoff = h_n_handoff.contiguous()
          c_n_handoff = c_n_handoff.contiguous()
        else:
          h_n_handoff = h_n_hindcast.contiguous()
          c_n_handoff = c_n_hindcast.contiguous()

        # DECODER
        if training:
            input = torch.unsqueeze(x_f[:,0,:], dim=1)
        else:
            input = torch.unsqueeze(x_h[:,-1,:], dim=1)

        lstm_output_forecast = torch.zeros(x_h.shape[0], self.forecast_length, self.nbr_features).to('cuda')
        hidden = h_n_handoff
        cell = c_n_handoff
        lstm_output_forecast[:,0] = input[:,0,:]
        for t in range(1, self.forecast_length):

            #insert input token embedding, previous hidden and previous cell states
            #receive output tensor (predictions) and new hidden and cell states
            output, (hidden, cell) = self.forecast_lstm(input, (hidden, cell))
            #place predictions in a tensor holding predictions for each token

            output = self.forecast_head(output)
            lstm_output_forecast[:,t] = output[:,0,:]

            if training:
              #decide if we are going to use teacher forcing or not
              teacher_force = random.random() < self.teacher_forcing_ratio

              #get the highest predicted token from our predictions

              #if teacher forcing, use actual next token as next input
              #if not, use predicted token
              input = torch.unsqueeze(x_f[:,t,:], dim=1) if teacher_force else output
            else:
              input = output
        # run forecast lstm

        # run heads for hindcast and forecast

        y_hindcast = lstm_output_forecast[:,0,0]#self.hindcast_head(self.dropout(lstm_output_hindcast))[:,-1,0]


        y_forecast = lstm_output_forecast[:,:,0]

        return y_hindcast, y_forecast

    def training_step(self, batch, batch_idx):

        x_h, x_f, y_h, y_f = batch


        if self.rnn_type == 'LSTM':
            y_hindcast, y_forecast = self._forward_path_LSTM(batch, training= True)
        elif self.rnn_type == 'GRU':
            y_hindcast, y_forecast = self._forward_path_GRU(batch, training= True)
        else:
            print(f'Error {self.rnn_type} is not implemented')

        loss_f = nn.functional.mse_loss(y_forecast, y_f)
        self.train_loss_f += loss_f
        self.nbr_iter += 1
        self.log("forecast_train_loss", loss_f)
        loss_h = nn.functional.mse_loss(y_hindcast, y_h[:,0])
        self.train_loss_h += loss_h
        self.log("hindacast_train_loss", loss_h)

        if self.fuse_loss:
          loss = (loss_f + loss_h)/2
        else:
          loss = loss_f
        return loss

    def validation_step(self, batch, batch_idx):

        x_h, y_f = batch
        y_h = y_f[:,0]

        if self.rnn_type == 'LSTM':
            y_hindcast, y_forecast = self._forward_path_LSTM(batch, training= False)
        elif self.rnn_type == 'GRU':
            y_hindcast, y_forecast = self._forward_path_GRU(batch, training= False)
        else:
            print(f'Error {self.rnn_type} is not implemented')

        loss_f = nn.functional.mse_loss(y_forecast, y_f)
        self.val_loss_f += loss_f
        self.nbr_iter_val += 1
        self.log("forecast_val_loss", loss_f)
        loss_h = nn.functional.mse_loss(y_hindcast, y_h)
        self.val_loss_h += loss_h
        self.log("hindacast_val_loss", loss_h)


    def forward(self, batch):

        if self.rnn_type == 'LSTM':
            y_hindcast, y_forecast = self._forward_path_LSTM(batch, training= False)
        elif self.rnn_type == 'GRU':
            y_hindcast, y_forecast = self._forward_path_GRU(batch, training= False)
        else:
            print(f'Error {self.rnn_type} is not implemented')

        return y_forecast

    def on_train_epoch_end(self):
      if self.fuse_loss:
        loss = (self.train_loss_f + self.train_loss_h) / self.nbr_iter
      else:
        loss = self.train_loss_f / self.nbr_iter
      #print(f'Traning loss: {loss}')
      self.log("mean_train_loss", loss)
      self.train_loss_f = 0
      self.train_loss_h = 0
      self.nbr_iter = 0

    def on_train_epoch_start(self):
      if self.nbr_iter_val:
        if self.fuse_loss:
          loss = (self.val_loss_f + self.val_loss_h) / self.nbr_iter_val
        else:
          loss = self.val_loss_f / self.nbr_iter_val
        #print(f'Validation loss: {loss}')
        self.log("mean_val_loss", loss)
        self.val_loss_f = 0
        self.val_loss_h = 0
        self.nbr_iter_val = 0

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=1e-3)



def define_model_ED(nbr_features, predict_ts, hindcast_hidden_size=256, forecast_hidden_size=256, handoff_hidden_size=256, hindcast_num_layers=2, forecast_num_layers=2, fuse_loss=False, dropout_prob=0.,head_type='regression', rnn_type='LSTM'):

  model = LitHindForeHandOff(
      input_size=nbr_features,
      hindcast_hidden_size = hindcast_hidden_size,
      hindcast_num_layers = hindcast_num_layers,
      forecast_hidden_size=forecast_hidden_size,
      forecast_num_layers = forecast_num_layers,
      handoff_hidden_size=handoff_hidden_size,
      forecast_length = predict_ts,
      fuse_loss = fuse_loss,
      dropout_prob=dropout_prob,
      head_type=head_type,
      rnn_type=rnn_type)
  return model

def training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = 30, save_epoch = 10, save_path=None, resume_path=None, log_output=True):
  savename_path = save_path 
  Path(savename_path).mkdir(parents=True, exist_ok=True)

  checkpoint_callback = ModelCheckpoint(dirpath=savename_path,
                                        every_n_epochs=save_epoch)
  if log_output:
    trainer = L.Trainer(max_epochs=nbr_epoch,
                        enable_model_summary=True,
                        callbacks=[checkpoint_callback],
                        val_check_interval=int(train_X_hindcast.shape[0]/batch_size),#
                        logger=comet_logger
                        )
  else:
    trainer = L.Trainer(max_epochs=nbr_epoch,
                        enable_model_summary=True,
                        callbacks=[checkpoint_callback],
                        val_check_interval=int(train_X_hindcast.shape[0]/batch_size)
                        )

  loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_X_forecast,train_y_hindcast, train_y), shuffle=True, batch_size=batch_size)
  test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=batch_size)
  if resume_path is None:
    trainer.fit(model=model, train_dataloaders=loader, val_dataloaders=test_loader)
  else:
    trainer.fit(model=model, train_dataloaders=loader, val_dataloaders=test_loader, ckpt_path=resume_path)
  loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_X_forecast,train_y_hindcast, train_y), shuffle=True, batch_size=1)
  test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

  print('train prediction')
  y_fit = trainer.predict(dataloaders=loader)
  print('test prediction')
  y_pred = trainer.predict(dataloaders=test_loader)

  return y_fit, y_pred, model

# LSTM

### Only WL

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="corrected_flood_lstm_wl",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = False
fuse_input = True


extra_in = []
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True


other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X = np.concatenate((train_X,past_train_x), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

    if train or load_model:
      train_X  = torch.tensor(train_X).float()
      train_y = torch.tensor(train_y).float()
      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()


      model = define_model_L(nbr_features, predict_ts-1, batch_size, nbr_hl)

      if load_model:
        model_load_path = base_drive_folder_path + 'weights/corrected_LP_interpolated_one_forecast_four_input_training_model/epoch=99-step=314199.ckpt'
        model = model.load_from_checkpoint(model_load_path)
        test_trainer = L.Trainer()
        train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
        test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

        y_fit = test_trainer.predict(model, dataloaders=train_loader)
        y_pred = test_trainer.predict(model, dataloaders=test_loader)

      if train:
        savename = 'corrected_LP_interpolated_one_forecast_four_input_training_model'
        y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 100, save_epoch = 10, save_path=savename)
      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled

    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="extended_corrected_flood_lstm_wl",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True


extra_in = []
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True


other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X = np.concatenate((train_X,past_train_x), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

    if train or load_model:
      train_X  = torch.tensor(train_X).float()
      train_y = torch.tensor(train_y).float()
      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()


      model = define_model_L(nbr_features, predict_ts-1, batch_size, nbr_hl)

      model_load_path = base_drive_folder_path + 'weights/corrected_LP_interpolated_one_forecast_four_input_training_model/epoch=99-step=314199.ckpt'
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          savename = 'corrected_LP_interpolated_one_forecast_four_input_training_model'
          y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 175, save_epoch = 10, save_path=savename, resume_path=model_load_path)


      else:
        savename = 'corrected_LP_interpolated_one_forecast_four_input_training_model'
        y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 100, save_epoch = 10, save_path=savename)
      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled

    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

### Preci

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="corrected_flood_lstm_wl_preci",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True


extra_in = [complete_df_preci]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X = np.concatenate((train_X,past_train_x), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

    if train or load_model:
      train_X  = torch.tensor(train_X).float()
      train_y = torch.tensor(train_y).float()
      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()


      model = define_model_L(nbr_features, predict_ts-1, batch_size, nbr_hl)

      if load_model:
        model_load_path = base_drive_folder_path + 'weights/LP_interpolated_preci_weather_one_forecast_four_input_training_model/epoch=99-step=314300.ckpt'
        model = model.load_from_checkpoint(model_load_path)
        test_trainer = L.Trainer()
        train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
        test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

        y_fit = test_trainer.predict(model, dataloaders=train_loader)
        y_pred = test_trainer.predict(model, dataloaders=test_loader)

      if train:
        savename = 'corrected_LP_interpolated_preci_one_forecast_four_input_training_model'
        y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 100, save_epoch = 10, save_path=savename)
      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled

    if train:
      if predict_ts > 1:
        print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
      else:
        print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
      compute_losses(y_train, y_fit, y_test, y_pred)

  break

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="extension_corrected_flood_lstm_wl_preci",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True


extra_in = [complete_df_preci]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X = np.concatenate((train_X,past_train_x), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

    if train or load_model:
      train_X  = torch.tensor(train_X).float()
      train_y = torch.tensor(train_y).float()
      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()


      model = define_model_L(nbr_features, predict_ts-1, batch_size, nbr_hl)
      model_load_path = base_drive_folder_path + 'weights/corrected_LP_interpolated_preci_one_forecast_four_input_training_model/epoch=99-step=314199-v1.ckpt'
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          savename = 'corrected_LP_interpolated_preci_one_forecast_four_input_training_model'
          y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 175, save_epoch = 10, save_path=savename, resume_path=model_load_path)


      else:
        savename = 'corrected_LP_interpolated_preci_one_forecast_four_input_training_model'
        y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 100, save_epoch = 10, save_path=savename)
      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled

    if train:
      if predict_ts > 1:
        print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
      else:
        print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
      compute_losses(y_train, y_fit, y_test, y_pred)

  break

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="extension2_corrected_flood_lstm_wl_preci",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True


extra_in = [complete_df_preci]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X = np.concatenate((train_X,past_train_x), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

    if train or load_model:
      train_X  = torch.tensor(train_X).float()
      train_y = torch.tensor(train_y).float()
      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()


      model = define_model_L(nbr_features, predict_ts-1, batch_size, nbr_hl)
      model_load_path = base_drive_folder_path + 'weights/corrected_LP_interpolated_preci_one_forecast_four_input_training_model/epoch=169-step=534139-v1.ckpt'
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          savename = 'corrected_LP_interpolated_preci_one_forecast_four_input_training_model'
          y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 250, save_epoch = 10, save_path=savename, resume_path=model_load_path)


      else:
        savename = 'corrected_LP_interpolated_preci_one_forecast_four_input_training_model'
        y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 100, save_epoch = 10, save_path=savename)
      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled

    if train:
      if predict_ts > 1:
        print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
      else:
        print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
      compute_losses(y_train, y_fit, y_test, y_pred)

  break

### Preci + temp

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="correct_flood_lstm_wl_preci_temp",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = False
fuse_input = True


extra_in = [complete_df_preci, complete_df_temp]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station
      other_station_id += list(complete_df_temp.columns)

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X = np.concatenate((train_X,past_train_x), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

    if train or load_model:
      train_X  = torch.tensor(train_X).float()
      train_y = torch.tensor(train_y).float()
      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()


      model = define_model_L(nbr_features, predict_ts-1, batch_size, nbr_hl)

      if load_model:
        model_load_path = base_drive_folder_path + 'weights/LP_interpolated_preci_weather_one_forecast_four_input_training_model/epoch=99-step=314300.ckpt'
        model = model.load_from_checkpoint(model_load_path)
        test_trainer = L.Trainer()
        train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
        test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

        y_fit = test_trainer.predict(model, dataloaders=train_loader)
        y_pred = test_trainer.predict(model, dataloaders=test_loader)

      if train:
        savename = 'correct_LP_interpolated_preci_weather_one_forecast_four_input_training_model'
        y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 100, save_epoch = 10, save_path=savename)
      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled

    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="extended_correct_flood_lstm_wl_preci_temp",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True


extra_in = [complete_df_preci, complete_df_temp]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station
      other_station_id += list(complete_df_temp.columns)

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X = np.concatenate((train_X,past_train_x), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

    if train or load_model:
      train_X  = torch.tensor(train_X).float()
      train_y = torch.tensor(train_y).float()
      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()


      model = define_model_L(nbr_features, predict_ts-1, batch_size, nbr_hl)

      model_load_path = base_drive_folder_path + 'ights/correct_LP_interpolated_preci_weather_one_forecast_four_input_training_model/epoch=99-step=314199.ckpt'
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          savename = 'correct_LP_interpolated_preci_weather_one_forecast_four_input_training_model'
          y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 250, save_epoch = 10, save_path=savename, resume_path=model_load_path)


      else:
        savename = 'correct_LP_interpolated_preci_weather_one_forecast_four_input_training_model'
        y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 100, save_epoch = 10, save_path=savename)
      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled

    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="extended2_correct_flood_lstm_wl_preci_temp",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True


extra_in = [complete_df_preci, complete_df_temp]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station
      other_station_id += list(complete_df_temp.columns)

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X = np.concatenate((train_X,past_train_x), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

    if train or load_model:
      train_X  = torch.tensor(train_X).float()
      train_y = torch.tensor(train_y).float()
      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()


      model = define_model_L(nbr_features, predict_ts-1, batch_size, nbr_hl)

      model_load_path = base_drive_folder_path + 'ghts/correct_LP_interpolated_preci_weather_one_forecast_four_input_training_model/epoch=249-step=785499.ckpt'
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          savename = 'correct_LP_interpolated_preci_weather_one_forecast_four_input_training_model'
          y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 350, save_epoch = 10, save_path=savename, resume_path=model_load_path)


      else:
        savename = 'correct_LP_interpolated_preci_weather_one_forecast_four_input_training_model'
        y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 100, save_epoch = 10, save_path=savename)
      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled

    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

# GRU

### Only WL

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="ex2_correct_flood_gru_wl",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True


extra_in = []
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True


other_station_id = None
predict_station_list = [0, 1, 2, 3]

nbr_epoch = 300

savename = 'corrected_GRU_interpolated_one_forecast_four_input_training_model'
load_path = base_drive_folder_path + 'weights/'
weight_name = 'epoch=199-step=628399.ckpt'

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X = np.concatenate((train_X,past_train_x), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

    if train or load_model:
      train_X  = torch.tensor(train_X).float()
      train_y = torch.tensor(train_y).float()
      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()

      model = define_model_L(nbr_features, predict_ts-1, batch_size, nbr_hl, rnn_type=['GRU'])

      if load_model:
        model_load_path = load_path + savename + '/' + weight_name

        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = nbr_epoch, save_epoch = 10, save_path=savename, resume_path = model_load_path)

      elif train:

        y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 100, save_epoch = 10, save_path=savename)
      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled

    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

### Preci

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="ex2_correct_last_flood_gru_wl_preci",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True

extra_in = [complete_df_preci]

complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True


other_station_id = None
predict_station_list = [0, 1, 2, 3]

nbr_epoch = 300

savename = 'corrected_GRU_interpolated_preci_one_forecast_four_input_training_model'
load_path = base_drive_folder_path + 'weights/'
weight_name = 'epoch=199-step=628399.ckpt'
#weight_name = 'epoch=99-step=314199.ckpt'


external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X = np.concatenate((train_X,past_train_x), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

    if train or load_model:
      train_X  = torch.tensor(train_X).float()
      train_y = torch.tensor(train_y).float()
      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()


      model = define_model_L(nbr_features, predict_ts-1, batch_size, nbr_hl, rnn_type=['GRU'])

      if load_model:
        model_load_path = load_path + savename + '/' + weight_name

        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = nbr_epoch, save_epoch = 10, save_path=savename, resume_path = model_load_path)

      elif train:

        y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 100, save_epoch = 10, save_path=savename)
      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled

    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

### preci + temp

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="ex_again_correct_flood_gru_wl_preci_temp",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20
nbr_hl = 256
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True

extra_in = [complete_df_preci, complete_df_temp]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

nbr_epoch = 200

savename = 'correct_GRU_interpolated_preci_weather_one_forecast_four_input_training_model'
load_path = base_drive_folder_path + 'ights/'
weight_name = 'epoch=199-step=628399.ckpt'
weight_name = 'epoch=99-step=314199.ckpt'


external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station
      other_station_id += list(complete_df_temp.columns)

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X, train_y, test_X, test_y, past_train_x, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X = np.concatenate((train_X,past_train_x), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)

    if train or load_model:
      train_X  = torch.tensor(train_X).float()
      train_y = torch.tensor(train_y).float()
      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()


      model = define_model_L(nbr_features, predict_ts-1, batch_size, nbr_hl, rnn_type=['GRU'])

      if load_model:
        model_load_path = load_path + savename + '/' + weight_name

        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X, train_y), shuffle=False, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = nbr_epoch, save_epoch = 10, save_path=savename, resume_path = model_load_path)

      elif train:

        y_fit, y_pred, model = training_model_L(model, batch_size,train_X, train_y, test_X, test_y, nbr_epoch = 100, save_epoch = 10, save_path=savename)
      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled

    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

# Encoder Decoder

## LSTM

### Again LSTM

#### Separated losses

**wl**

100 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.92
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.81

200 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -1.00
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.78


#### Fuse loses

**wl**

100 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.95
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.84

200 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.93
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.81

 **preci & wl**

 100 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.92
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.80

200 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.96
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.80

#### wl

In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = True
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True

log_output = False
if train:
  log_output = True
log_output = False

if log_output:
  comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="ex_nohindhead_correct_flood_fuseloss_ED_LSTM_wl_20h",  # Optional flood_ED_HO_wl
  )

max_epoch = 200
rnn_type='LSTM'
savename = 'nohindhead_correct_flood_fuseloss_ED_LSTM_wl_20h/'
load_model_name = 'epoch=199-step=628399.ckpt'

save_path = base_drive_folder_path + 'ights/' + savename
model_load_path = save_path + load_model_name

extra_in = []
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression', rnn_type=rnn_type)
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path, log_output=log_output)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, log_output=log_output)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

#### Preci

In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = True
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True

if train:
  log_output = True

if log_output:
  comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="ex4_nohindhead_correct_flood_fuseloss_ED_LSTM_preci_wl_20h"#nohindhead_correct_flood_fuseloss_ED_GRU_preci_wl_20h",  # Optional flood_ED_HO_wl
  )

max_epoch = 300
rnn_type='LSTM'
savename = 'nohindhead_correct_flood_fuseloss_ED_LSTM_preci_wl_20h/'
load_model_name = 'epoch=199-step=628399.ckpt'

save_path = base_drive_folder_path + 'ghts/' + savename
model_load_path = save_path + load_model_name

extra_in = [complete_df_preci]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]
    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name



    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression', rnn_type=rnn_type)
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path, log_output=log_output)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, log_output=log_output)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

### Results Only stations

#### **LSTM**
Epoch 100
Training:
 MAE: 0.02 MSE: 0.03 NSE: 0.95
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.81

Epoch 175
Training:
 MAE: 0.01 MSE: 0.02 NSE: 0.96
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.79
#### **Encoder Decoder separate losses**

Prediction for station 1007639 with a forecast of 10 hours and a lookback of 19 hours.

100 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.96
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.75

200 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.98
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.79

300 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.99
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.79

#### **Encoder Decoder fuse losses**

Prediction for station 1007639 with a forecast of 10 hours and a lookback of 19 hours.

100 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.91
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.82

200 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.93
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.77


 #### **Encoder Decoder fuse losses**

 **Preci and wl**

 Encoder decoder lstm


100 epochs
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.87
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.84


180 epochs
 Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.96
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.85

250 epochs
Overfit

**Preci, temp and wl**

100 epochs
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.87
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.83


180 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.94
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.80

### Basic

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="correct_flood_ED_wl_20h",  # Optional flood_ED_HO_wl
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = False
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = False
fuse_input = True

max_epoch = 100

savename = 'correct_LP_ED_noHO_interpolated_one_forecast_four_input_training_model_20h/'
load_model_name = 'epoch=99-step=314199.ckpt'
save_path = base_drive_folder_path + 'ghts/' + savename
model_load_path = save_path + load_model_name

extra_in = []
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression')
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = False
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = False
norm_input = True
load_model = True
fuse_input = True

max_epoch = 100

savename = 'correct_LP_ED_noHO_interpolated_one_forecast_four_input_training_model_20h/'
load_model_name = 'epoch=99-step=314199.ckpt'
save_path = base_drive_folder_path + 'ghts/' + savename
model_load_path = save_path + load_model_name

extra_in = []
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression')
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="extended_correct_flood_ED_wl_20h",  # Optional flood_ED_HO_wl
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = False
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = False
norm_input = True
load_model = True
fuse_input = True

max_epoch = 200

savename = 'correct_LP_ED_noHO_interpolated_one_forecast_four_input_training_model_20h/'
load_model_name = 'epoch=199-step=628399.ckpt'
save_path = base_drive_folder_path + 'ights/' + savename
model_load_path = save_path + load_model_name

extra_in = []
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression')
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="extended2_correct_flood_ED_wl_20h",  # Optional flood_ED_HO_wl
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = False
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = False
norm_input = True
load_model = True
fuse_input = True

max_epoch = 300

savename = 'correct_LP_ED_noHO_interpolated_one_forecast_four_input_training_model_20h/'
load_model_name = 'epoch=299-step=942599.ckpt'
save_path = base_drive_folder_path + 'ghts/' + savename
model_load_path = save_path + load_model_name

extra_in = []
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression')
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

### Fuse Input

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="extended_fuse_correct_flood_ED_wl_20h",  # Optional flood_ED_HO_wl
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = True
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = False
norm_input = True
load_model = True
fuse_input = True

max_epoch = 200

savename = 'correct_fuse_LP_ED_noHO_interpolated_one_forecast_four_input_training_model_20h/'
load_model_name = 'epoch=199-step=628399.ckpt'
save_path = base_drive_folder_path + 'weights/' + savename
model_load_path = save_path + load_model_name

extra_in = []
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression')
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

### Preci and wl fuse

LSTM


100 epochs
Training:
 MAE: 0.02 MSE: 0.03 NSE: 0.95
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.78

175 epochs
Training:
 MAE: 0.01 MSE: 0.02 NSE: 0.97
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.82

250 epochs
Training:
 MAE: 0.01 MSE: 0.02 NSE: 0.98
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.81


Encoder decoder lstm


100 epochs
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.87
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.84


180 epochs
 Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.96
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.85

250 epochs
Overfit

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="extended3_fuse_preci_correct_flood_ED_wl_20h",  # Optional flood_ED_HO_wl
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = True
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = False
norm_input = True
load_model = True
fuse_input = True

max_epoch = 250

savename = 'correct_fuse_LP_ED_noHO_interpolated_one_forecast_preci_four_input_training_model_20h/'
load_model_name = 'epoch=249-step=785499.ckpt'
save_path = base_drive_folder_path + 'weights/' + savename
model_load_path = save_path + load_model_name

extra_in = [complete_df_preci]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]
    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression')
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

### Preci wl and temp

Encoder decoder lstm


100 epochs
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.87
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.83


180 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.94
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.80

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="fuse_preci_temp_correct_flood_ED_wl_20h",  # Optional flood_ED_HO_wl
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = True
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = False
norm_input = True
load_model = True
fuse_input = True

max_epoch = 180

savename = 'correct_fuse_LP_ED_noHO_interpolated_one_forecast_preci_temp_four_input_training_model_20h/'
load_model_name = 'Copie de epoch=99-step=314199.ckpt' #
load_model_name = 'epoch=179-step=565559.ckpt'
save_path = base_drive_folder_path + 'weights/' + savename
model_load_path = save_path + load_model_name

extra_in = [complete_df_preci, complete_df_temp]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]
    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station
      other_station_id += list(complete_df_temp.columns)


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression')
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

## GRU

### Only wl

In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = True
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True

log_output = False
if train:
  log_output = True

if log_output:
  comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="nohindhead_cecorrect_flood_fuseloss_ED_GRU_wl_20h",  # Optional flood_ED_HO_wl
  )

max_epoch = 200
rnn_type='GRU'
savename = 'nohindhead_cecorrect_flood_fuseloss_ED_GRU_wl_20h/'
load_model_name = 'epoch=99-step=314199.ckpt'

save_path = base_drive_folder_path + 'weights/' + savename
model_load_path = save_path + load_model_name

extra_in = []
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression', rnn_type=rnn_type)
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path, log_output=log_output)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, log_output=log_output)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

# LSTM Encoder decoder Handoff

**wl fuse losses Handoff**

100 epochs:
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.88
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.82


180 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -1.00
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.83

250 epochs:
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.89
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.80

**Preci and wl fuse losses Handoff**

100 epochs
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.88
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.85


180 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.94
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.85


250 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.92
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.83

**Preci, temp and wl fuse losses Handoff**


180 epochs:
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.84
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.83


250 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.94
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.79

### Only WL

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="correct_GRU_flood_ED_HO_wl",  # Optional flood_ED_HO_wl
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = 256
h_num_layers = 2
f_num_layers = 2

fuse_loss = True
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = False
norm_input = True
load_model = True
fuse_input = True

max_epoch = 250

savename = 'correct_fuse_LP_ED_256HO_interpolated_one_forecast_four_input_training_model_20h/'

load_model_name = 'epoch=249-step=785499.ckpt'
#load_model_name = 'epoch=179-step=565559.ckpt'
#load_model_name = 'epoch=99-step=314199.ckpt'


save_path = base_drive_folder_path + 'weights/' + savename
model_load_path = save_path + load_model_name

extra_in = []
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]
    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression')
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

### Preci wl fuse loss

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="extended3_correct_flood_ED_HO_wl_fuseloss",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = 256
h_num_layers = 2
f_num_layers = 2

fuse_loss = True
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = False
norm_input = True
load_model = True
fuse_input = True

max_epoch = 250

savename = 'correct_fuse_LP_ED_256HO_interpolated_one_forecast_preci_four_input_training_model_20h/'
load_model_name = 'epoch=249-step=785499.ckpt'

save_path = base_drive_folder_path + 'eights/' + savename
model_load_path = save_path + load_model_name

extra_in = [complete_df_preci]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]
    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression')
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

### Preci + temp

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="extended3_correct_flood_ED_HO_wl_preci_temp",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = 256
h_num_layers = 2
f_num_layers = 2

fuse_loss = True
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = False
norm_input = True
load_model = True
fuse_input = True

max_epoch = 250

savename = 'correct_fuse_LP_ED_256HO_interpolated_one_forecast_preci_temp_four_input_training_model_20h/'
load_model_name = 'Copie de epoch=179-step=565559.ckpt'

save_path = base_drive_folder_path + 'weights/' + savename
model_load_path = save_path + load_model_name

extra_in = [complete_df_preci, complete_df_temp]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:

    predict_station = wl_station[predict_station_id]
    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station
      other_station_id += list(complete_df_temp.columns)


      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED(nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho, hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers, fuse_loss=fuse_loss, dropout_prob=0.,head_type='regression')
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

# Results


## LSTM
**wl**


100 epochs:
Training:
 MAE: 0.02 MSE: 0.03 NSE: 0.95
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.81


175 epochs:
Training:
 MAE: 0.01 MSE: 0.02 NSE: 0.96
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.79

**Preci and wl**


100 epochs:
Training:
 MAE: 0.02 MSE: 0.03 NSE: 0.95
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.78

175 epochs:
Training:
 MAE: 0.01 MSE: 0.02 NSE: 0.97
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.82

250 epochs:
Training:
 MAE: 0.01 MSE: 0.02 NSE: 0.98
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.81


 **Preci, temp and wl**


100 epochs:
Training:
 MAE: 0.02 MSE: 0.02 NSE: 0.96
Testing:
 MAE: 0.04 MSE: 0.08 NSE: 0.66

250 epochs:
Training:
 MAE: 0.01 MSE: 0.01 NSE: 0.99
Testing:
 MAE: 0.03 MSE: 0.07 NSE: 0.75

350 epochs:
Training:
 MAE: 0.01 MSE: 0.01 NSE: 1.00
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.78

## GRU

**wl**

100 epochs:
Training:
 MAE: 0.02 MSE: 0.03 NSE: 0.95
Testing:
 MAE: 0.04 MSE: 0.08 NSE: 0.59

200 epochs:
Training:
 MAE: 0.02 MSE: 0.04 NSE: 0.86
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.78

300 epochs:
Training:
 MAE: 0.02 MSE: 0.04 NSE: 0.89
Testing:
 MAE: 0.03 MSE: 0.08 NSE: 0.64

**Preci and wl**

100 epochs:
Training:
 MAE: 0.02 MSE: 0.03 NSE: 0.95
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.79


200 epochs:
Training:
 MAE: 0.02 MSE: 0.04 NSE: 0.89
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.83

300 epochs:
Training:
 MAE: 0.02 MSE: 0.03 NSE: 0.92
Testing:
 MAE: 0.04 MSE: 0.10 NSE: 0.41

**Preci, temp and wl**

100 epochs:
Training:
 MAE: 0.02 MSE: 0.05 NSE: 0.84
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.83

200 epochs:
Training:
 MAE: 0.02 MSE: 0.03 NSE: 0.95
Testing:
 MAE: 0.03 MSE: 0.07 NSE: 0.76

250 epochs:
Training:
 MAE: 0.02 MSE: 0.03 NSE: 0.95
Testing:
 MAE: 0.03 MSE: 0.08 NSE: 0.66


## Encoder Decoder separate losses
### LSTM
**wl**


100 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.96
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.75


200 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.98
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.79

300 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.99
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.79

### GRU

**wl**

100 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -1.00
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.81

200 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -1.10
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.78


## Encoder Decoder fuse losses

### GRU

**wl**

100 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.93
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.83

200 epochs:
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.86
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.83

### LSTM
**wl**

100 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.91
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.82

200 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.93
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.77


 **Preci and wl**

 Encoder decoder lstm


100 epochs
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.87
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.84


180 epochs
 Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.96
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.85

250 epochs
Overfit

**Preci, temp and wl**

100 epochs
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.87
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.83


180 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.94
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.80

**wl fuse losses Handoff**

100 epochs:
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.88
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.82


180 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -1.00
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.83

250 epochs:
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.89
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.80

 **Preci and wl fuse losses Handoff**

100 epochs
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.88
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.85


180 epochs
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.94
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.85


250 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.92
Testing:
 MAE: 0.02 MSE: 0.05 NSE: 0.83

 **Preci, temp and wl fuse losses Handoff**


180 epochs:
Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.84
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.83


250 epochs:
Training:
 MAE: 0.10 MSE: 0.17 NSE: -0.94
Testing:
 MAE: 0.03 MSE: 0.06 NSE: 0.79

# Attention Please

## Definitions

In [ ]:
import torch.nn.functional as F
import random

class Attention(L.LightningModule):
    def __init__(self, past_ts, hidden_size=256, nbr_features=7, decoder=None, head=None, batch_first=True, mode='concat',dropout = .2):
        super(Attention, self).__init__()

        self.hidden_size = hidden_size
        self.batch_first = batch_first

        self.decoder_rnn = decoder
        self.head = head
        self.mode = mode
        if  self.mode =='luong':
          self.score_linear = nn.Linear(hidden_size , hidden_size)

        elif self.mode == 'concat' or self.mode == 'bahdanau':
          self.score_linear = nn.Linear(hidden_size*2 , hidden_size)
          self.v = torch.nn.Parameter(torch.FloatTensor(hidden_size))

        self.attention_linear = nn.Linear(hidden_size*2 , hidden_size)


        self.att_weights = nn.Parameter(torch.Tensor(1, hidden_size), requires_grad=True)
        self.dropout = nn.Dropout(dropout)

        stdv = 1.0 / np.sqrt(self.hidden_size)
        for weight in self.att_weights:
            nn.init.uniform_(weight, -stdv, stdv)

    def get_mask(self):
        pass

    def forward(self, enc_hidden, prev_hidden, dec_output):
      # input: encoder hiddens states, decoder hiden state, decoder output

        if self.mode == 'luong':
          mult = (prev_hidden[-1].unsqueeze(1))*self.score_linear(enc_hidden)
          score = torch.sum(mult, dim=2)

        elif self.mode == 'dot':
          score = torch.sum(enc_hidden*prev_hidden[-1].unsqueeze(1), dim=2)

        elif self.mode == 'concat' or self.mode == 'bahdanau':
          prev_hidden_ex = prev_hidden[-1].unsqueeze(1).expand(-1, enc_hidden.shape[1], -1)

          energy = torch.cat((prev_hidden_ex, enc_hidden), 2)
          score = torch.sum(self.v * self.score_linear(energy).tanh(), dim=2)

        att_w = F.softmax(score, dim=0)

        # compute attention weights
        att_w = torch.unsqueeze(att_w, dim=2)

        # compute attention output
        att_out = torch.bmm(enc_hidden.transpose(1,2), att_w).transpose(1,2)

        att_cat = torch.cat((prev_hidden[-1].unsqueeze(1), att_out), dim=2)

        # compute prediction
        if self.mode == 'luong' or self.mode == 'concat' or self.mode == 'dot':

          cats = self.attention_linear(att_cat)

          output = self.head(cats.tanh().squeeze(0))
          return output, prev_hidden

        elif self.mode == 'bahdanau':
          return att_cat, prev_hidden

class LitAttentionHindForeHandOff_OLD(L.LightningModule):
    def __init__(self,
                 input_size=10,
                 hindcast_hidden_size = 256,
                 hindcast_num_layers = 2,
                 forecast_hidden_size=256,
                 forecast_num_layers = 2,
                 handoff_hidden_size=None,
                 forecast_length = 10,
                 past_ts = 19,
                 fuse_loss = False,
                 dropout_prob=0.,
                 head_type='regression',
                 rnn_type='GRU',
                 attention_mode = 'luong',
                 teacher_forcing_ratio = .5):
        super().__init__()

        self.forecast_length = forecast_length
        self.nbr_features = input_size
        self.hindcast_hidden_size = hindcast_hidden_size
        self.hindcast_num_layers = hindcast_num_layers


        if rnn_type == 'LSTM':
          self.hindcast_lstm = nn.LSTM(
              input_size=input_size,
              hidden_size=self.hindcast_hidden_size,
              num_layers=self.hindcast_num_layers,
              batch_first=True
              )
        elif rnn_type == 'GRU':
          if attention_mode == 'bahdanau':
            self.hindcast_lstm = nn.GRU(
                input_size=input_size,
                hidden_size=self.hindcast_hidden_size,
                num_layers=self.hindcast_num_layers,
                batch_first=True,
                bidirectional = True
                )
          else:
            self.hindcast_lstm = nn.GRU(
                input_size=input_size,
                hidden_size=self.hindcast_hidden_size,
                num_layers=self.hindcast_num_layers,
                batch_first=True
                )

        self.forecast_hidden_size = forecast_hidden_size
        self.forecast_num_layers = forecast_num_layers

        if rnn_type == 'LSTM':
          self.forecast_lstm = nn.LSTM(
              input_size=input_size,
              hidden_size=self.forecast_hidden_size,
              num_layers=self.forecast_num_layers,
              batch_first=True
              )
        elif rnn_type == 'GRU':
          self.forecast_lstm = nn.GRU(
              input_size=input_size,
              hidden_size=self.forecast_hidden_size,
              num_layers=self.forecast_num_layers,
              batch_first=True
              )


        if handoff_hidden_size is not None:
          self.handoff_net = nn.Sequential(
              *[nn.Linear(self.hindcast_hidden_size*2, handoff_hidden_size),
              nn.ReLU(),
              nn.Dropout(p=0.)]
              )

          self.handoff_linear = nn.Sequential(
              *[nn.Linear(handoff_hidden_size, self.forecast_hidden_size*2),
              nn.Dropout(p=0.)]
              )
        else:
          self.handoff_net = None

        self.dropout = nn.Dropout(p=dropout_prob)

        if head_type == 'regression':
          self.hindcast_head = nn.Sequential(nn.Linear(self.hindcast_hidden_size, input_size))#, nn.ReLU())
          self.forecast_head = nn.Sequential(nn.Linear(self.forecast_hidden_size, self.nbr_features))#, nn.ReLU())

        self.attn = Attention(past_ts, forecast_hidden_size,nbr_features=self.nbr_features, decoder=self.forecast_lstm, head=self.forecast_head, mode=attention_mode)

        self.fuse_loss = fuse_loss

        self.teacher_forcing_ratio = teacher_forcing_ratio

        self.train_loss_f = 0
        self.train_loss_h = 0
        self.nbr_iter = 0
        self.val_loss = 0

        self.val_loss_f = 0
        self.val_loss_h = 0
        self.nbr_iter_val = 0


    def training_step(self, batch, batch_idx):
        x_h, x_f, y_h, y_f = batch

        # run the hindcast lstm
        lstm_output_hindcast, h_n_hindcast = self.hindcast_lstm(x_h)
        #lstm_output_hindcast = lstm_output_hindcast.transpose(0, 1)

        h_n_handoff = h_n_hindcast.contiguous()

# DECODER
        input = torch.unsqueeze(x_f[:,0,:], dim=1)

        lstm_output_forecast = torch.zeros(x_h.shape[0], self.forecast_length, self.nbr_features).to('cuda')
        hidden = h_n_handoff
        lstm_output_forecast[:,0] = input[:,0,:]

        for t in range(1, self.forecast_length):
            #insert input token embedding, previous hidden and previous cell states
            #receive output tensor (predictions) and new hidden and cell states
            if self.attn.mode != 'bahdanau':

              output, hidden = self.forecast_lstm(input, hidden)

              input, hidden = self.attn(lstm_output_hindcast, hidden, output)

            elif self.attn.mode == 'bahdanau':

              context, hidden = self.attn(lstm_output_hindcast, hidden, input)
              x_input = torch.cat((context, torch.unsqueeze(input, dim=1)), dim=-1)
              input, hidden = self.forecast_lstm(x_input, hidden)
              input = self.forecast_head(input)

            lstm_output_forecast[:,t] = input[:,0,:]

            #decide if we are going to use teacher forcing or not
            teacher_force = random.random() < self.teacher_forcing_ratio

            #get the highest predicted token from our predictions

            #if teacher forcing, use actual next token as next input
            #if not, use predicted token
            input = torch.unsqueeze(x_f[:,t,:], dim=1) if teacher_force else input
        # run forecast lstm

        # run heads for hindcast and forecast

        y_forecast = lstm_output_forecast[:,:,0]


        loss_f = nn.functional.mse_loss(y_forecast, y_f)
        self.train_loss_f += loss_f
        self.nbr_iter += 1
        self.log("forecast_train_loss", loss_f)


        if self.fuse_loss:
          y_hindcast = self.hindcast_head(self.dropout(lstm_output_hindcast))[:,-1,0]
          loss_h = nn.functional.mse_loss(y_hindcast, y_h[:,0])
          self.train_loss_h += loss_h
          self.log("hindacast_train_loss", loss_h)
          loss = (loss_f + loss_h)/2
        else:
          loss = loss_f
        return loss

    def validation_step(self, batch, batch_idx):
        x_h, y_f = batch
        y_h = y_f[:,0]
        # run the hindcast lstm
        lstm_output_hindcast, h_n_hindcast = self.hindcast_lstm(x_h)

        #print(f'hindcast x {x_h.shape} \n hincast output {lstm_output_hindcast.shape} \n hidden hindcast {h_n_hindcast.shape}')

        if self.handoff_net is not None:
          x = self.handoff_net(h_n_hindcast)
          initial_state = self.handoff_linear(x)
          h_n_handoff = initial_state.contiguous()
        else:
          h_n_handoff = h_n_hindcast.contiguous()

        # DECODER
        input = torch.unsqueeze(x_h[:,-1,:], dim=1)

        lstm_output_forecast = torch.zeros(x_h.shape[0], self.forecast_length, self.nbr_features).to('cuda')
        hidden = h_n_handoff
        lstm_output_forecast[:,0] = input[:,0,:]

        for t in range(1, self.forecast_length):
            #insert input token embedding, previous hidden and previous cell states
            #receive output tensor (predictions) and new hidden and cell states
            if self.attn.mode != 'bahdanau':

              output, hidden = self.forecast_lstm(input, hidden)

              input, hidden = self.attn(lstm_output_hindcast, hidden, output)

            elif self.attn.mode == 'bahdanau':

              context, hidden = self.attn(lstm_output_hindcast, hidden, input)
              x_input = torch.cat((context, torch.unsqueeze(input, dim=1)), dim=-1)
              input, hidden = self.forecast_lstm(x_input, hidden)
              input = self.forecast_head(input)

            lstm_output_forecast[:,t] = input[:,0,:]

        # run heads for hindcast and forecast
        y_forecast = lstm_output_forecast[:,:,0]

        loss_f = nn.functional.mse_loss(y_forecast, y_f)
        self.val_loss_f += loss_f
        self.nbr_iter_val += 1
        self.log("forecast_val_loss", loss_f)

        if self.fuse_loss:
          y_hindcast = self.hindcast_head(self.dropout(lstm_output_hindcast))[:,-1,0]
          loss_h = nn.functional.mse_loss(y_hindcast, y_h)
          self.val_loss_h += loss_h
          self.log("hindacast_val_loss", loss_h)


    def forward(self, batch):
        if len(batch) == 2:
          x_h, y_f = batch
        else:
          x_h, x_f, y_h, y_f = batch

        y_h = y_f[:,0]
        # run the hindcast lstm
        lstm_output_hindcast, h_n_hindcast = self.hindcast_lstm(x_h)
        #lstm_output_hindcast = lstm_output_hindcast.transpose(0, 1)

        # handoff initial state to forecast lstm
        if self.handoff_net is not None:
          x = self.handoff_net(h_n_hindcast)
          initial_state = self.handoff_linear(x)
          h_n_handoff, c_n_handoff = initial_state.chunk(2, -1)
          h_n_handoff = h_n_handoff.contiguous()
        else:
          h_n_handoff = h_n_hindcast.contiguous()

        # DECODER
        input = torch.unsqueeze(x_h[:,-1,:], dim=1)

        lstm_output_forecast = torch.zeros(x_h.shape[0], self.forecast_length, self.nbr_features).to('cuda')
        lstm_output_forecast = torch.zeros(x_h.shape[0], self.forecast_length, self.nbr_features).to('cuda')
        hidden = h_n_handoff
        lstm_output_forecast[:,0] = input[:,0,:]

        for t in range(1, self.forecast_length):
            #insert input token embedding, previous hidden and previous cell states
            #receive output tensor (predictions) and new hidden and cell states
            if self.attn.mode != 'bahdanau':

              output, hidden = self.forecast_lstm(input, hidden)

              input, hidden = self.attn(lstm_output_hindcast, hidden, output)

            elif self.attn.mode == 'bahdanau':

              context, hidden = self.attn(lstm_output_hindcast, hidden, input)
              x_input = torch.cat((context, torch.unsqueeze(input, dim=1)), dim=-1)
              input, hidden = self.forecast_lstm(x_input, hidden)
              input = self.forecast_head(input)

            if len(input.shape) < 3:
              input = torch.unsqueeze(input, dim=0)
            lstm_output_forecast[:,t] = input[:,0,:]

        # run heads for hindcast and forecast
        y_hindcast = self.hindcast_head(self.dropout(lstm_output_hindcast))[:,-1,0]
        y_forecast = lstm_output_forecast[:,:,0]
        return y_forecast

    def on_train_epoch_end(self):
      if self.fuse_loss:
        loss = (self.train_loss_f + self.train_loss_h) / self.nbr_iter
      else:
        loss = self.train_loss_f / self.nbr_iter
      #print(f'Traning loss: {loss}')
      self.log("mean_train_loss", loss)
      self.train_loss_f = 0
      self.train_loss_h = 0
      self.nbr_iter = 0

    def on_train_epoch_start(self):
      if self.nbr_iter_val:
        if self.fuse_loss:
          loss = (self.val_loss_f + self.val_loss_h) / self.nbr_iter_val
        else:
          loss = self.val_loss_f / self.nbr_iter_val
        #print(f'Validation loss: {loss}')
        self.log("mean_val_loss", loss)
        self.val_loss_f = 0
        self.val_loss_h = 0
        self.nbr_iter_val = 0

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=1e-3)



def define_model_ED_Attn(past_ts, nbr_features, predict_ts, hindcast_hidden_size=256, forecast_hidden_size=256, handoff_hidden_size=256, hindcast_num_layers=2, forecast_num_layers=2, fuse_loss=False, dropout_prob=0.,head_type='regression', rnn_type='GRU', attention_mode='luong'):

  model = LitAttentionHindForeHandOff(
      input_size=nbr_features,
      hindcast_hidden_size = hindcast_hidden_size,
      hindcast_num_layers = hindcast_num_layers,
      forecast_hidden_size=forecast_hidden_size,
      forecast_num_layers = forecast_num_layers,
      handoff_hidden_size=handoff_hidden_size,
      forecast_length = predict_ts,
      past_ts = past_ts,
      fuse_loss = fuse_loss,
      dropout_prob=dropout_prob,
      head_type=head_type,
      rnn_type=rnn_type,
      attention_mode = attention_mode)
  return model

def training_model_ED_Attn(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = 30, save_epoch = 10, save_path=None, resume_path=None):
  savename_path = save_path #base_drive_folder_path + 'eights/' + save_path + '/'
  Path(savename_path).mkdir(parents=True, exist_ok=True)

  checkpoint_callback = ModelCheckpoint(dirpath=savename_path,
                                        every_n_epochs=save_epoch)
  trainer = L.Trainer(max_epochs=nbr_epoch,
                      enable_model_summary=True,
                      callbacks=[checkpoint_callback],
                      val_check_interval=int(train_X_hindcast.shape[0]/batch_size),
                      logger=comet_logger
                      )

  loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_X_forecast,train_y_hindcast, train_y), shuffle=True, batch_size=batch_size)
  test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=batch_size)
  if resume_path is None:
    trainer.fit(model=model, train_dataloaders=loader, val_dataloaders=test_loader)
  else:
    trainer.fit(model=model, train_dataloaders=loader, val_dataloaders=test_loader, ckpt_path=resume_path)
  loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_X_forecast,train_y_hindcast, train_y), shuffle=True, batch_size=1)
  test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

  y_fit = trainer.predict(dataloaders=loader)
  y_pred = trainer.predict(dataloaders=test_loader)

  return y_fit, y_pred, model

In [ ]:
import torch.nn.functional as F
import random

class Attention(L.LightningModule):
    def __init__(self, past_ts, hidden_size=256, nbr_features=7, decoder=None, head=None, batch_first=True, mode='concat',dropout = .2):
        super(Attention, self).__init__()

        self.hidden_size = hidden_size
        self.batch_first = batch_first

        self.decoder_rnn = decoder
        self.head = head
        self.mode = mode
        if  self.mode =='luong':
          self.score_linear = nn.Linear(hidden_size , hidden_size)

        elif self.mode == 'concat' or self.mode == 'bahdanau':
          self.score_linear = nn.Linear(hidden_size*2 , hidden_size)
          self.v = torch.nn.Parameter(torch.FloatTensor(hidden_size))

        self.attention_linear = nn.Linear(hidden_size*2 , hidden_size)


        self.att_weights = nn.Parameter(torch.Tensor(1, hidden_size), requires_grad=True)
        self.dropout = nn.Dropout(dropout)

        stdv = 1.0 / np.sqrt(self.hidden_size)
        for weight in self.att_weights:
            nn.init.uniform_(weight, -stdv, stdv)

    def get_mask(self):
        pass

    def forward(self, enc_hidden, prev_hidden, dec_output):
      # input: encoder hiddens states, decoder hiden state, decoder output

        if self.mode == 'luong':
          mult = (prev_hidden[-1].unsqueeze(1))*self.score_linear(enc_hidden)
          score = torch.sum(mult, dim=2)

        elif self.mode == 'dot':
          score = torch.sum(enc_hidden*prev_hidden[-1].unsqueeze(1), dim=2)

        elif self.mode == 'concat' or self.mode == 'bahdanau':
          prev_hidden_ex = prev_hidden[-1].unsqueeze(1).expand(-1, enc_hidden.shape[1], -1)

          energy = torch.cat((prev_hidden_ex, enc_hidden), 2)
          score = torch.sum(self.v * self.score_linear(energy).tanh(), dim=2)

        att_w = F.softmax(score, dim=0)

        # compute attention weights
        att_w = torch.unsqueeze(att_w, dim=2)

        # compute attention output
        att_out = torch.bmm(enc_hidden.transpose(1,2), att_w).transpose(1,2)

        att_cat = torch.cat((prev_hidden[-1].unsqueeze(1), att_out), dim=2)

        # compute prediction
        if self.mode == 'luong' or self.mode == 'concat' or self.mode == 'dot':

          cats = self.attention_linear(att_cat)

          output = self.head(cats.tanh().squeeze(0))
          return output, prev_hidden

        elif self.mode == 'bahdanau':
          return att_cat, prev_hidden

class LitAttentionHindForeHandOff(L.LightningModule):
    def __init__(self,
                 input_size=10,
                 hindcast_hidden_size = 256,
                 hindcast_num_layers = 2,
                 forecast_hidden_size=256,
                 forecast_num_layers = 2,
                 handoff_hidden_size=None,
                 forecast_length = 10,
                 past_ts = 19,
                 fuse_loss = False,
                 dropout_prob=0.,
                 head_type='regression',
                 rnn_type='GRU',
                 attention_mode = 'luong',
                 teacher_forcing_ratio = .5):
        super().__init__()

        self.forecast_length = forecast_length
        self.nbr_features = input_size
        self.hindcast_hidden_size = hindcast_hidden_size
        self.hindcast_num_layers = hindcast_num_layers


        if rnn_type == 'LSTM':
          self.hindcast_lstm = nn.LSTM(
              input_size=input_size,
              hidden_size=self.hindcast_hidden_size,
              num_layers=self.hindcast_num_layers,
              batch_first=True
              )
        elif rnn_type == 'GRU':
          if attention_mode == 'bahdanau':
            self.hindcast_lstm = nn.GRU(
                input_size=input_size,
                hidden_size=self.hindcast_hidden_size,
                num_layers=self.hindcast_num_layers,
                batch_first=True,
                bidirectional = True
                )
          else:
            self.hindcast_lstm = nn.GRU(
                input_size=input_size,
                hidden_size=self.hindcast_hidden_size,
                num_layers=self.hindcast_num_layers,
                batch_first=True
                )

        self.forecast_hidden_size = forecast_hidden_size
        self.forecast_num_layers = forecast_num_layers

        if rnn_type == 'LSTM':
          self.forecast_lstm = nn.LSTM(
              input_size=input_size,
              hidden_size=self.forecast_hidden_size,
              num_layers=self.forecast_num_layers,
              batch_first=True
              )
        elif rnn_type == 'GRU':
          self.forecast_lstm = nn.GRU(
              input_size=input_size,
              hidden_size=self.forecast_hidden_size,
              num_layers=self.forecast_num_layers,
              batch_first=True
              )


        if handoff_hidden_size is not None:
          self.handoff_net = nn.Sequential(
              *[nn.Linear(self.hindcast_hidden_size*2, handoff_hidden_size),
              nn.ReLU(),
              nn.Dropout(p=0.)]
              )

          self.handoff_linear = nn.Sequential(
              *[nn.Linear(handoff_hidden_size, self.forecast_hidden_size*2),
              nn.Dropout(p=0.)]
              )
        else:
          self.handoff_net = None

        self.dropout = nn.Dropout(p=dropout_prob)

        if head_type == 'regression':
          self.hindcast_head = nn.Sequential(nn.Linear(self.hindcast_hidden_size, input_size))#, nn.ReLU())
          self.forecast_head = nn.Sequential(nn.Linear(self.forecast_hidden_size, self.nbr_features))#, nn.ReLU())

        self.attn = Attention(past_ts, forecast_hidden_size,nbr_features=self.nbr_features, decoder=self.forecast_lstm, head=self.forecast_head, mode=attention_mode)

        self.fuse_loss = fuse_loss

        self.teacher_forcing_ratio = teacher_forcing_ratio

        self.train_loss_f = 0
        self.train_loss_h = 0
        self.nbr_iter = 0
        self.val_loss = 0

        self.val_loss_f = 0
        self.val_loss_h = 0
        self.nbr_iter_val = 0

    def _training_path(self, batch, training):
        if len(batch) == 2:
            x_h, y_f = batch
            y_h = y_f[:,0]
        else:
            x_h, x_f, y_h, y_f = batch

        # run the hindcast lstm
        lstm_output_hindcast, h_n_hindcast = self.hindcast_lstm(x_h)
        #lstm_output_hindcast = lstm_output_hindcast.transpose(0, 1)

        h_n_handoff = h_n_hindcast.contiguous()

        # DECODER
        input = torch.unsqueeze(x_f[:,0,:], dim=1)

        lstm_output_forecast = torch.zeros(x_h.shape[0], self.forecast_length, self.nbr_features).to('cuda')
        hidden = h_n_handoff
        lstm_output_forecast[:,0] = input[:,0,:]

        for t in range(1, self.forecast_length):
            #insert input token embedding, previous hidden and previous cell states
            #receive output tensor (predictions) and new hidden and cell states
            if self.attn.mode != 'bahdanau':

              output, hidden = self.forecast_lstm(input, hidden)

              input, hidden = self.attn(lstm_output_hindcast, hidden, output)

            elif self.attn.mode == 'bahdanau':

              context, hidden = self.attn(lstm_output_hindcast, hidden, input)
              x_input = torch.cat((context, torch.unsqueeze(input, dim=1)), dim=-1)
              input, hidden = self.forecast_lstm(x_input, hidden)
              input = self.forecast_head(input)

            lstm_output_forecast[:,t] = input[:,0,:]
            if training:
                #decide if we are going to use teacher forcing or not
                teacher_force = random.random() < self.teacher_forcing_ratio

                #get the highest predicted token from our predictions

                #if teacher forcing, use actual next token as next input
                #if not, use predicted token
                input = torch.unsqueeze(x_f[:,t,:], dim=1) if teacher_force else input
            else:
                if len(input.shape) < 3:
                    input = torch.unsqueeze(input, dim=0)
        # run forecast lstm

        # run heads for hindcast and forecast

        y_forecast = lstm_output_forecast[:,:,0]
        y_hindcast = lstm_output_forecast[:,0,0]#self.hindcast_head(self.dropout(lstm_output_hindcast))[:,-1,0]

        return y_hindcast, y_forecast

    def training_step(self, batch, batch_idx):

        y_hindcast, y_forecast = self._training_path(batch, True)

        loss_f = nn.functional.mse_loss(y_forecast, y_f)
        self.train_loss_f += loss_f
        self.nbr_iter += 1
        self.log("forecast_train_loss", loss_f)


        if self.fuse_loss:
          loss_h = nn.functional.mse_loss(y_hindcast, y_h[:,0])
          self.train_loss_h += loss_h
          self.log("hindacast_train_loss", loss_h)
          loss = (loss_f + loss_h)/2
        else:
          loss = loss_f
        return loss

    def validation_step(self, batch, batch_idx):

        y_hindcast, y_forecast = self._training_path(batch, False)

        loss_f = nn.functional.mse_loss(y_forecast, y_f)
        self.val_loss_f += loss_f
        self.nbr_iter_val += 1
        self.log("forecast_val_loss", loss_f)

        if self.fuse_loss:
          loss_h = nn.functional.mse_loss(y_hindcast, y_h)
          self.val_loss_h += loss_h
          self.log("hindacast_val_loss", loss_h)


    def forward(self, batch):

        y_hindcast, y_forecast = self._training_path(batch, False)

        return y_forecast

    def on_train_epoch_end(self):
      if self.fuse_loss:
        loss = (self.train_loss_f + self.train_loss_h) / self.nbr_iter
      else:
        loss = self.train_loss_f / self.nbr_iter
      #print(f'Traning loss: {loss}')
      self.log("mean_train_loss", loss)
      self.train_loss_f = 0
      self.train_loss_h = 0
      self.nbr_iter = 0

    def on_train_epoch_start(self):
      if self.nbr_iter_val:
        if self.fuse_loss:
          loss = (self.val_loss_f + self.val_loss_h) / self.nbr_iter_val
        else:
          loss = self.val_loss_f / self.nbr_iter_val
        #print(f'Validation loss: {loss}')
        self.log("mean_val_loss", loss)
        self.val_loss_f = 0
        self.val_loss_h = 0
        self.nbr_iter_val = 0

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=1e-3)



def define_model_ED_Attn(past_ts, nbr_features, predict_ts, hindcast_hidden_size=256, forecast_hidden_size=256, handoff_hidden_size=256, hindcast_num_layers=2, forecast_num_layers=2, fuse_loss=False, dropout_prob=0.,head_type='regression', rnn_type='GRU', attention_mode='luong'):

  model = LitAttentionHindForeHandOff(
      input_size=nbr_features,
      hindcast_hidden_size = hindcast_hidden_size,
      hindcast_num_layers = hindcast_num_layers,
      forecast_hidden_size=forecast_hidden_size,
      forecast_num_layers = forecast_num_layers,
      handoff_hidden_size=handoff_hidden_size,
      forecast_length = predict_ts,
      past_ts = past_ts,
      fuse_loss = fuse_loss,
      dropout_prob=dropout_prob,
      head_type=head_type,
      rnn_type=rnn_type,
      attention_mode = attention_mode)
  return model

def training_model_ED_Attn(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = 30, save_epoch = 10, save_path=None, resume_path=None):
  savename_path = save_path #base_drive_folder_path + 'weights/' + save_path + '/'
  Path(savename_path).mkdir(parents=True, exist_ok=True)

  checkpoint_callback = ModelCheckpoint(dirpath=savename_path,
                                        every_n_epochs=save_epoch)
  trainer = L.Trainer(max_epochs=nbr_epoch,
                      enable_model_summary=True,
                      callbacks=[checkpoint_callback],
                      val_check_interval=int(train_X_hindcast.shape[0]/batch_size),
                      logger=comet_logger
                      )

  loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_X_forecast,train_y_hindcast, train_y), shuffle=True, batch_size=batch_size)
  test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=batch_size)
  if resume_path is None:
    trainer.fit(model=model, train_dataloaders=loader, val_dataloaders=test_loader)
  else:
    trainer.fit(model=model, train_dataloaders=loader, val_dataloaders=test_loader, ckpt_path=resume_path)
  loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_X_forecast,train_y_hindcast, train_y), shuffle=True, batch_size=1)
  test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

  y_fit = trainer.predict(dataloaders=loader)
  y_pred = trainer.predict(dataloaders=test_loader)

  return y_fit, y_pred, model

## Training

### wl and preci

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="attn_floss_bahdanau_flood_ED_HO_wl_preci",  # Optional
)

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="TEST",  # Optional
)

In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 20

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = False
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = False
fuse_input = True

max_epoch = 100
attn_mode = 'bahdanau'#, concat
savename = 'attn_floss_bahdanau_LP_ED_interpolated_one_forecast_preci_four_input_training_model_20h/'

load_model_name = 'epoch=199-step=628399.ckpt'
save_path = base_drive_folder_path + 'weights/' + savename
model_load_path = save_path + load_model_name


extra_in = [complete_df_preci]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED_Attn(past_ts, nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho,
                                   hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers,
                                   fuse_loss=fuse_loss, dropout_prob=0.,
                                   head_type='regression', rnn_type='GRU', attention_mode=attn_mode)
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED_Attn(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED_Attn(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

#### **Fuse Loss**


Prediction for station 1007639 with a forecast of 10 hours and a lookback of 19 hours.

**dot**


dot
100 epochs:


Training:
 MAE: 0.25 MSE: 0.29 NSE: -5.05
Testing:
 MAE: 0.23 MSE: 0.24 NSE: -2.45

 200 epcohs

 Training:
 MAE: 0.22 MSE: 0.26 NSE: -3.78
Testing:
 MAE: 0.18 MSE: 0.20 NSE: -1.22

300 epochs

Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.74
Testing:
 MAE: 0.05 MSE: 0.08 NSE: 0.65

400 epochs;

Training:
 MAE: 0.31 MSE: 0.34 NSE: -7.11
Testing:
 MAE: 0.31 MSE: 0.33 NSE: -5.20



 **Luong**

 200 epochs:

Training:
 MAE: 0.12 MSE: 0.19 NSE: -1.41
Testing:
 MAE: 0.12 MSE: 0.15 NSE: -0.30

300 epochs:

Training:
 MAE: 0.38 MSE: 0.42 NSE: -11.83
Testing:
 MAE: 0.37 MSE: 0.38 NSE: -7.80

**concat**

 200 epochs:

Training:
 MAE: 0.40 MSE: 0.43 NSE: -12.60
Testing:
 MAE: 0.38 MSE: 0.39 NSE: -7.76

300 epochs:

Training:
 MAE: 0.14 MSE: 0.19 NSE: -1.69
Testing:
 MAE: 0.13 MSE: 0.16 NSE: -0.51


400 epochs:

Training:
 MAE: 0.12 MSE: 0.17 NSE: -1.02
Testing:
 MAE: 0.09 MSE: 0.11 NSE: 0.30

#### **Only forecast loss**


#### dot

100 epochs:

Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.87
Testing:
 MAE: 0.10 MSE: 0.15 NSE: -0.26

200 epochs:

Training:
 MAE: 0.11 MSE: 0.17 NSE: -1.10
Testing:
 MAE: 0.11 MSE: 0.16 NSE: -0.39

 #### luong

 100 epochs:

Training:
 MAE: 0.10 MSE: 0.15 NSE: -0.63
Testing:
 MAE: 0.05 MSE: 0.11 NSE: 0.32

200 epochs:

Training:
 MAE: 0.11 MSE: 0.15 NSE: -0.58
Testing:
 MAE: 0.11 MSE: 0.14 NSE: -0.20

 #### concat

 not convincing

### wl preci and temp

In [ ]:
# arguments made to CometLogger are passed on to the comet_ml.Experiment class
comet_logger = CometLogger(
    api_key=YOUR_API_KEY,
    project_name="flood-prediction",  # Optional
    experiment_name="exagain_attn_floss_luong_flood_ED_HO_wl_preci_temp",  # Optional
)

INFO: CometLogger will be initialized in online mode
INFO:lightning.pytorch.loggers.comet:CometLogger will be initialized in online mode


In [ ]:
import logging

logging.getLogger("lightning.pytorch.utilities.rank_zero").setLevel(logging.WARNING)
logging.getLogger("lightning.pytorch.accelerators.cuda").setLevel(logging.WARNING)


# TODO complete this for correct prediction
train_ratio = 0.75
batch_size = 14

nbr_hl_f = 256
nbr_hl_h = 256
nbr_hl_ho = None
h_num_layers = 2
f_num_layers = 2

fuse_loss = False
past_ts=19
forecast_ts_list=[11]#[i for i in range(1,13)]
train = True
norm_input = True
load_model = True
fuse_input = True

max_epoch = 200
attn_mode = 'luong'#, concat
savename = 'attn_floss_luong_fuse_LP_ED_interpolated_one_forecast_preci_temp_four_input_training_model_20h/'

load_model_name = 'epoch=99-step=448899.ckpt'
save_path = base_drive_folder_path + 'weights/' + savename
model_load_path = save_path + load_model_name


extra_in = [complete_df_preci, complete_df_temp]
complete_df_inter_train = complete_df_inter.copy()

if len(extra_in) > 1:
  fuse_input = True

other_station_id = None
predict_station_list = [0, 1, 2, 3]

external_inputs = None#list(complete_df_preci.columns)+ list(complete_df_temp.columns)
for predict_station_id in predict_station_list:
  for predict_ts in forecast_ts_list:
    predict_station = wl_station[predict_station_id]

    if fuse_input:
      other_input_station = predict_station_list.copy()
      other_input_station.pop(predict_station_id)

      other_station_id = [wl_station[i] for i in other_input_station]

      complete_df_inter_train.drop(columns=complete_df_inter_train.columns[len(predict_station_list):], axis=1, inplace=True)
      other_station_id += preci_station
      other_station_id += list(complete_df_temp.columns)

      df_fused = pd.concat([complete_df_inter_train]+ extra_in, axis=1)
    else:
      df_fused = complete_df_inter_train.copy()

    train_ts = df_fused.iloc[int(train_ratio*df_fused.shape[0])].name


    df_train = df_fused.loc[:train_ts].iloc[:,predict_station_id:]
    df_test = df_fused.loc[train_ts:].iloc[:,predict_station_id:]
    nbr_features = df_train.columns.unique().shape[0]


    if norm_input:
      # define minmax scaler
      scale_wl = MinMaxScale(df_train, ul=1, ll=-1)

      # scale the train and test data
      df_train_scaled = scale_wl.NormMM(df_train)
      df_test_scaled = scale_wl.NormMM(df_test)
    else:
      df_train_scaled = df_train
      df_test_scaled = df_test

    reframed_train = series_to_supervised(df_train_scaled, past_ts, predict_ts)#.diff()[1:]
    reframed_test = series_to_supervised(df_test_scaled, past_ts, predict_ts)#.diff()[1:]
    train_X_hindcast, train_X_forecast, train_y, test_X, test_y, past_train_x_hindcast, past_train_x_forecast, past_train_y, past_test_x, past_test_y, test_X_pd = prepare_past_stages_ED_windows(reframed_train, reframed_test, predict_ts, past_ts, nbr_features, external_inputs, predict_station, other_station_id)

    if fuse_input:
      train_X_hindcast = np.concatenate((train_X_hindcast,past_train_x_hindcast), axis=2)
      train_X_forecast = np.concatenate((train_X_forecast,past_train_x_forecast), axis=2)
      test_X = np.concatenate((test_X,past_test_x), axis=2)

    train_y_hindcast = train_X_forecast[:,0,:].copy()

    y_train_scaled = reframed_train.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    y_test_scaled = reframed_test.iloc[:, (past_ts*nbr_features+1):].filter(regex=predict_station)
    if train or load_model:
      train_X_hindcast  = torch.tensor(train_X_hindcast).float()
      train_X_forecast  = torch.tensor(train_X_forecast).float()

      train_y = torch.tensor(train_y).float()
      train_y_hindcast = torch.tensor(train_y_hindcast).float()

      test_X =  torch.tensor(test_X).float()
      test_y = torch.tensor(test_y).float()




      model = define_model_ED_Attn(past_ts, nbr_features, predict_ts-1, hindcast_hidden_size=nbr_hl_h, forecast_hidden_size=nbr_hl_f, handoff_hidden_size=nbr_hl_ho,
                                   hindcast_num_layers=h_num_layers, forecast_num_layers=f_num_layers,
                                   fuse_loss=fuse_loss, dropout_prob=0.,
                                   head_type='regression', rnn_type='GRU', attention_mode=attn_mode)
      if load_model:
        if not train:
          model = model.load_from_checkpoint(model_load_path)
          test_trainer = L.Trainer()
          train_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(train_X_hindcast, train_y), shuffle=True, batch_size=1)
          test_loader = torch.utils.data.DataLoader(torch.utils.data.TensorDataset(test_X, test_y), shuffle=False, batch_size=1)

          y_fit = test_trainer.predict(model, dataloaders=train_loader)
          y_pred = test_trainer.predict(model, dataloaders=test_loader)
        else:
          y_fit, y_pred, model = training_model_ED_Attn(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path, resume_path=model_load_path)

      elif train:
        y_fit, y_pred, model = training_model_ED_Attn(model, batch_size, train_X_hindcast, train_X_forecast, train_y_hindcast, train_y, test_X, test_y, nbr_epoch = max_epoch, save_epoch = 10, save_path=save_path)

      y_fit = torch.stack(y_fit).squeeze()
      y_pred = torch.stack(y_pred).squeeze()

      y_fit_scaled = pd.DataFrame(y_fit, index=y_train_scaled.index, columns=y_train_scaled.columns)
      y_pred_scaled = pd.DataFrame(y_pred, index=y_test_scaled.index, columns=y_test_scaled.columns)
      if norm_input:
        y_fit   = scale_wl.DeNormMM(y_fit_scaled, predict_station)
        y_pred  = scale_wl.DeNormMM(y_pred_scaled, predict_station)
      else:
        y_fit = y_fit_scaled
        y_pred = y_pred_scaled

    if norm_input:
      y_train = scale_wl.DeNormMM(y_train_scaled, predict_station)
      y_test  = scale_wl.DeNormMM(y_test_scaled, predict_station)
    else:
      y_train = y_train_scaled
      y_test = y_test_scaled


    if predict_ts > 1:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hours and a lookback of {past_ts} hours.')
    else:
      print(f'Prediction for station {predict_station} with a forecast of {predict_ts-1} hour and a lookback of {past_ts} hours.')
    compute_losses(y_train, y_fit, y_test, y_pred)

  break

### **Fuse loss**

Prediction for station 1007639 with a forecast of 10 hours and a lookback of 19 hours.

### dot


dot
200 epochs:

Training:
 MAE: 0.12 MSE: 0.19 NSE: -1.59
Testing:
 MAE: 0.08 MSE: 0.12 NSE: 0.1

 300 epcohs:

Training:
 MAE: 0.18 MSE: 0.22 NSE: -2.48
Testing:
 MAE: 0.16 MSE: 0.19 NSE: -1.01

 ### Luong

 100 epochs:

Training:
 MAE: 0.23 MSE: 0.27 NSE: -4.16
Testing:
 MAE: 0.18 MSE: 0.20 NSE: -1.31

200 epochs

Training:
 MAE: 0.39 MSE: 0.43 NSE: -13.21
Testing:
 MAE: 0.31 MSE: 0.37 NSE: -7.44

### **Forecast loss**

**dot**

100 epochs:

Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.79
Testing:
 MAE: 0.06 MSE: 0.09 NSE: 0.50

200 epochs:

Training:
 MAE: 0.15 MSE: 0.20 NSE: -1.98
Testing:
 MAE: 0.10 MSE: 0.12 NSE: 0.10

 **luong**

 100 epochs:

Training:
 MAE: 0.11 MSE: 0.19 NSE: -1.46
Testing:
 MAE: 0.08 MSE: 0.14 NSE: -0.30

 **concat**

 100 epochs:

Training:
 MAE: 0.11 MSE: 0.19 NSE: -1.46
Testing:
 MAE: 0.08 MSE: 0.14 NSE: -0.30

200 epochs:

Training:
 MAE: 0.10 MSE: 0.16 NSE: -0.86
Testing:
 MAE: 0.02 MSE: 0.06 NSE: 0.76
